# Boulevard Gardens - Data Cleaning
### By Julia-Simone Rutgers

This notebook includes steps to clean two datasets:
- property assessment data for the Wolseley neighbourhood in Winnipeg
- and a shoeleather dataset of neighbourhood properties that have planted boulevard gardens

The data will be used to analyse whether these boulevard gardens are more prevalent in 'wealthier' parts of the neighbourhood. _(In this story, relative 'wealth' is signalled by higher average property values)_


Methodology for the garden data collection is explained later in the document.

In [1]:
# Document set up
import pandas as pd
import numpy as np

In [2]:
# Read in assessment parcels - Wolseley
df = pd.read_csv("Assessment_Parcels_Wolseley.csv")

#### What's the data?

Assessment parcels for properties in the Wolseley neighbourhood area, sourced from [Winnipeg Open Data](https://data.winnipeg.ca/Assessment-Taxation-Corporate/Assessment-Parcels/d4mq-wa44/explore/query/SELECT%0A%20%20%60roll_number%60%2C%0A%20%20%60street_number%60%2C%0A%20%20%60unit_number%60%2C%0A%20%20%60street_direction%60%2C%0A%20%20%60street_name%60%2C%0A%20%20%60street_type%60%2C%0A%20%20%60full_address%60%2C%0A%20%20%60neighbourhood_area%60%2C%0A%20%20%60property_use_code%60%2C%0A%20%20%60assessed_land_area%60%2C%0A%20%20%60zoning%60%2C%0A%20%20%60total_assessed_value%60%2C%0A%20%20%60assessment_date%60%2C%0A%20%20%60detail_url%60%2C%0A%20%20%60current_assessment_year%60%2C%0A%20%20%60property_class_1%60%2C%0A%20%20%60geometry%60%2C%0A%20%20%60centroid_lat%60%2C%0A%20%20%60centroid_lon%60%0AWHERE%20caseless_eq%28%60neighbourhood_area%60%2C%20%22WOLSELEY%22%29/page/column_manager). The data has been filtered to include only Wolseley properties. It has also been trimmed to return only columns for the address (street number, street name, street type, etc.), total assessed property values, zoning/property use identifiers (there are a few), and geometry. The roll number is used as a unique identifier.

In [3]:
df.head()

Roll Number  Street Number Unit Number Street Direction Street Name  \
0  12080201000         1430.0         NaN              NaN     PORTAGE   
1  12080240200         1420.0         NaN              NaN     PORTAGE   
2  12080250500            NaN         NaN              NaN      RAGLAN   
3  12080260000          542.0         NaN              NaN      RAGLAN   
4  12080261000          538.0         NaN              NaN      RAGLAN   

  Street Type         Full Address Neighbourhood Area  \
0      AVENUE  1430 PORTAGE AVENUE           WOLSELEY   
1      AVENUE  1420 PORTAGE AVENUE           WOLSELEY   
2        ROAD          RAGLAN ROAD           WOLSELEY   
3        ROAD      542 RAGLAN ROAD           WOLSELEY   
4        ROAD      538 RAGLAN ROAD           WOLSELEY   

                  Property Use Code  Assessed Land Area  \
0        PIRPK - PARK WITH BUILDING            488220.0   
1                    PIICH - CHURCH             88446.0   
2      VRES1 - VACANT RESIDENTIAL 1            141149.0   
3  RESSD - DETACHED SINGLE DWELLING              5997.0   
4  RESSD - DETACHED SINGLE DWELLING              5997.0   

                   Zoning  Total Assessed Value         Assessment Date  \
0  PR1 - PRKS&REC-PASSIVE             3130000.0  04/01/2023 12:00:00 AM   
1   R2 - RES - TWO FAMILY             3144000.0  04/01/2023 12:00:00 AM   
2   R2 - RES - TWO FAMILY              518000.0  04/01/2023 12:00:00 AM   
3   R2 - RES - TWO FAMILY              305000.0  04/01/2023 12:00:00 AM   
4   R2 - RES - TWO FAMILY              364000.0  04/01/2023 12:00:00 AM   

                                          Detail URL  Current Assessment Year  \
0  http://www.winnipegassessment.com/asmtpub/engl...                     2026   
1  http://www.winnipegassessment.com/asmtpub/engl...                     2026   
2  http://www.winnipegassessment.com/asmtpub/engl...                     2026   
3  http://www.winnipegassessment.com/AsmtPub/engl...                     2026   
4  http://www.winnipegassessment.com/AsmtPub/engl...                     2026   

  Property Class 1                                           Geometry  \
0            OTHER  MULTIPOLYGON (((-97.19095901066672 49.87922629...   
1    INSTITUTIONAL  MULTIPOLYGON (((-97.19158825669882 49.88158128...   
2    RESIDENTIAL 1  MULTIPOLYGON (((-97.19107262988514 49.88077998...   
3    RESIDENTIAL 1  MULTIPOLYGON (((-97.19102616382078 49.88138204...   
4    RESIDENTIAL 1  MULTIPOLYGON (((-97.19102616382078 49.88138204...   

   Centroid Lat  Centroid Lon  
0     49.879843    -97.192867  
1     49.881477    -97.191951  
2     49.880161    -97.191705  
3     49.881459    -97.191275  
4     49.881322    -97.191286

#### Data Cleaning:

I am simultaneously looking at these parcels in geojson, where it's a bit easier to understand some of the complexities of the data. 
I want to trim out parcels that are not homes or businesses. I also want to consolidate condos/apartments to one property. Zoning is not the easiest column to use for categorization, as some properties are zoned residential but being used as businesses, or zoned R2 but do not have a building on them (they're greenspace, for example). Property use code is most specific for this kind of analysis.


In [4]:
# First, clean up column names:

df.columns = df.columns.str.lower()
df.columns = df.columns.str.replace(' ', '_')
df.head(1)

roll_number  street_number unit_number street_direction street_name  \
0  12080201000         1430.0         NaN              NaN     PORTAGE   

  street_type         full_address neighbourhood_area  \
0      AVENUE  1430 PORTAGE AVENUE           WOLSELEY   

            property_use_code  assessed_land_area                  zoning  \
0  PIRPK - PARK WITH BUILDING            488220.0  PR1 - PRKS&REC-PASSIVE   

   total_assessed_value         assessment_date  \
0             3130000.0  04/01/2023 12:00:00 AM   

                                          detail_url  current_assessment_year  \
0  http://www.winnipegassessment.com/asmtpub/engl...                     2026   

  property_class_1                                           geometry  \
0            OTHER  MULTIPOLYGON (((-97.19095901066672 49.87922629...   

   centroid_lat  centroid_lon  
0     49.879843    -97.192867

In [5]:
# Grab the basic information about our table:

df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2671 entries, 0 to 2670
Data columns (total 19 columns):
 #   Column                   Non-Null Count  Dtype  
---  ------                   --------------  -----  
 0   roll_number              2671 non-null   int64  
 1   street_number            2656 non-null   float64
 2   unit_number              148 non-null    object 
 3   street_direction         149 non-null    object 
 4   street_name              2664 non-null   object 
 5   street_type              2655 non-null   object 
 6   full_address             2664 non-null   object 
 7   neighbourhood_area       2671 non-null   object 
 8   property_use_code        2671 non-null   object 
 9   assessed_land_area       2516 non-null   float64
 10  zoning                   2523 non-null   object 
 11  total_assessed_value     2656 non-null   float64
 12  assessment_date          2671 non-null   object 
 13  detail_url               2671 non-null   object 
 14  current_assessment_year 

In [6]:
# From scanning the data, I know that not all properties have a street number (house number)
# From the map, I know many are parks, etc. 
# I want the number so I can keep track of my cleaning success. 
df.street_number.isnull().value_counts()

street_number
False    2656
True       15
Name: count, dtype: int64

In [7]:
# What do those 15 look like?

In [8]:
df[df.street_number.isnull()]

roll_number  street_number unit_number street_direction street_name  \
2     12080250500            NaN         NaN              NaN      RAGLAN   
7     12080264000            NaN         NaN              NaN      RAGLAN   
8     12080264500            NaN         NaN              NaN      RAGLAN   
551   12081002500            NaN         NaN              NaN         NaN   
563   12081013500            NaN         NaN              NaN         NaN   
570   12081020500            NaN         NaN              NaN         NaN   
1311  12081918000            NaN         NaN              NaN        RUBY   
1453  12082098000            NaN         NaN              NaN        RUBY   
1479  12082127000            NaN         NaN              NaN     EVANSON   
1503  12082156200            NaN         NaN              NaN         NaN   
2236  12083106000            NaN         NaN              NaN         NaN   
2275  12083157000            NaN         NaN              NaN         NaN   
2283  12083166500            NaN         NaN              NaN         NaN   
2471  12090217000            NaN         NaN              NaN     ALLOWAY   
2629  12097751300            NaN         NaN              NaN     PURCELL   

     street_type    full_address neighbourhood_area  \
2           ROAD     RAGLAN ROAD           WOLSELEY   
7           ROAD     RAGLAN ROAD           WOLSELEY   
8           ROAD     RAGLAN ROAD           WOLSELEY   
551          NaN             NaN           WOLSELEY   
563          NaN             NaN           WOLSELEY   
570          NaN             NaN           WOLSELEY   
1311      STREET     RUBY STREET           WOLSELEY   
1453      STREET     RUBY STREET           WOLSELEY   
1479      STREET  EVANSON STREET           WOLSELEY   
1503         NaN             NaN           WOLSELEY   
2236         NaN             NaN           WOLSELEY   
2275         NaN             NaN           WOLSELEY   
2283         NaN             NaN           WOLSELEY   
2471      AVENUE  ALLOWAY AVENUE           WOLSELEY   
2629      AVENUE  PURCELL AVENUE           WOLSELEY   

                 property_use_code  assessed_land_area  \
2     VRES1 - VACANT RESIDENTIAL 1            141149.0   
7     VRES1 - VACANT RESIDENTIAL 1              5997.0   
8     VRES1 - VACANT RESIDENTIAL 1              2399.0   
551         REFRL - REFERENCE ROLL               124.0   
563         REFRL - REFERENCE ROLL               415.0   
570         REFRL - REFERENCE ROLL              1259.0   
1311  VRES1 - VACANT RESIDENTIAL 1              2272.0   
1453  VRES1 - VACANT RESIDENTIAL 1              2954.0   
1479  VRES1 - VACANT RESIDENTIAL 1                24.0   
1503  VRES1 - VACANT RESIDENTIAL 1              1874.0   
2236        REFRL - REFERENCE ROLL                 1.0   
2275        REFRL - REFERENCE ROLL                 1.0   
2283  VRES2 - VACANT RESIDENTIAL 2                41.0   
2471  VRES1 - VACANT RESIDENTIAL 1                68.0   
2629         CNCMP - CONDO COMPLEX                 NaN   

                         zoning  total_assessed_value         assessment_date  \
2         R2 - RES - TWO FAMILY              518000.0  04/01/2023 12:00:00 AM   
7         R2 - RES - TWO FAMILY              283000.0  04/01/2023 12:00:00 AM   
8         R2 - RES - TWO FAMILY              230000.0  04/01/2023 12:00:00 AM   
551       R2 - RES - TWO FAMILY                   NaN  04/01/2023 12:00:00 AM   
563       R2 - RES - TWO FAMILY                   NaN  04/01/2023 12:00:00 AM   
570       R2 - RES - TWO FAMILY                   NaN  04/01/2023 12:00:00 AM   
1311      R2 - RES - TWO FAMILY              226000.0  04/01/2023 12:00:00 AM   
1453      R2 - RES - TWO FAMILY              220000.0  04/01/2023 12:00:00 AM   
1479      R2 - RES - TWO FAMILY                  50.0  04/01/2023 12:00:00 AM   
1503      R2 - RES - TWO FAMILY                3117.0  04/01/2023 12:00:00 AM   
2236      R2 - RES - TWO FAMILY                   NaN  04/01/2023 12:00:

In [9]:
# Let's look at the unique property_use_code
df.property_use_code.unique()

array(['PIRPK - PARK WITH BUILDING', 'PIICH - CHURCH',
       'VRES1 - VACANT RESIDENTIAL 1', 'RESSD - DETACHED SINGLE DWELLING',
       'CMOFF - OFFICE', 'CMRST - STORE',
       'RESMC - MULTIFAMILY CONVERSION',
       'RESSU - RESIDENTIAL SECONDARY UNIT',
       'RESMA - MULTIPLE ATTACHED UNITS',
       'CMVSR - VEHICLE SERVICE RELATED', 'RESDU - DUPLEX',
       'CMFBK - BANK', 'PIISC - SCHOOL', 'CMRCV - CONVENIENCE STORE',
       'CMRRE - RESTAURANT', 'REFRL - REFERENCE ROLL',
       'RESAP - APARTMENTS', 'CMSTP - STRIP MALL',
       'RESGC - RESIDENTIAL GROUP CARE', 'CMPSP - SURFACE PARKING',
       'RESMU - RESIDENTIAL MULTIPLE USE',
       'CMCMU - COMMERCIAL MULTIPLE USE', 'PIRCC - COMMUNITY CENTRE',
       'RESTR - TRIPLEX', 'CNCMP - CONDO COMPLEX',
       'CNRES - CONDO RESIDENTIAL', 'CMOMC - MEDICAL OFFICE CLINIC',
       'RESAM - APARTMENTS MULTIPLE USE',
       'PIIGC - NON-RESIDENTIAL GROUP CARE',
       'CMMRH - COMMERCIAL ROW HOUSE',
       'RESMB - RESIDENTIAL MULTIPLE 

In [10]:
# From looking at the mapped version, I know vacant residentials are mostly parks or non-buildings. 
# Does the count of vacants match the null street numbers count?

df.property_use_code.str.contains("VRES").value_counts()

property_use_code
False    2648
True       23
Name: count, dtype: int64

In [11]:
# There are more! Okay. Let's see them too.
df[df.property_use_code.str.contains("VRES")]

roll_number  street_number unit_number street_direction  street_name  \
2     12080250500            NaN         NaN              NaN       RAGLAN   
7     12080264000            NaN         NaN              NaN       RAGLAN   
8     12080264500            NaN         NaN              NaN       RAGLAN   
34    12080305500          534.0         NaN              NaN        CRAIG   
236   12080530000         1270.0         NaN              NaN     WOLSELEY   
701   12081184000         1064.0         NaN              NaN   PALMERSTON   
704   12081189100          104.0         NaN                S     GARFIELD   
919   12081435000         1020.0         NaN              NaN   PALMERSTON   
989   12081510000           35.0         NaN              NaN       AUBREY   
990   12081519200          139.0         NaN              NaN       AUBREY   
1222  12081806000           49.0         NaN              NaN       LENORE   
1223  12081807000           55.0         NaN              NaN       LENORE   
1311  12081918000            NaN         NaN              NaN         RUBY   
1453  12082098000            NaN         NaN              NaN         RUBY   
1479  12082127000            NaN         NaN              NaN      EVANSON   
1503  12082156200            NaN         NaN              NaN          NaN   
1596  12082275000          165.0         NaN              NaN      EVANSON   
1915  12082721100          850.0         NaN              NaN   PALMERSTON   
1968  12082784000          852.0         NaN              NaN  WESTMINSTER   
2283  12083166500            NaN         NaN              NaN          NaN   
2462  12090208000           17.0         NaN              NaN      ALLOWAY   
2471  12090217000            NaN         NaN              NaN      ALLOWAY   
2523  12097511500          547.0           1              NaN       NEWMAN   

     street_type            full_address neighbourhood_area  \
2           ROAD             RAGLAN ROAD           WOLSELEY   
7           ROAD             RAGLAN ROAD           WOLSELEY   
8           ROAD             RAGLAN ROAD           WOLSELEY   
34        STREET        534 CRAIG STREET           WOLSELEY   
236       AVENUE    1270 WOLSELEY AVENUE           WOLSELEY   
701       AVENUE  1064 PALMERSTON AVENUE           WOLSELEY   
704       STREET   104 GARFIELD STREET S           WOLSELEY   
919       AVENUE  1020 PALMERSTON AVENUE           WOLSELEY   
989       STREET        35 AUBREY STREET           WOLSELEY   
990       STREET       139 AUBREY STREET           WOLSELEY   
1222      STREET        49 LENORE STREET           WOLSELEY   
1223      STREET        55 LENORE STREET           WOLSELEY   
1311      STREET             RUBY STREET           WOLSELEY   
1453      STREET             RUBY STREET           WOLSELEY   
1479      STREET          EVANSON STREET           WOLSELEY   
1503         NaN                     NaN           WOLSELEY   
1596      STREET      165 EVANSON STREET           WOLSELEY   
1915      AVENUE   850 PALMERSTON AVENUE           WOLSELEY   
1968      AVENUE  852 WESTMINSTER AVENUE           WOLSELEY   
2283         NaN                     NaN           WOLSELEY   
2462      AVENUE       17 ALLOWAY AVENUE           WOLSELEY   
2471      AVENUE          ALLOWAY AVENUE           WOLSELEY   
2523      STREET     1-547 NEWMAN STREET           WOLSELEY   

                 property_use_code  assessed_land_area                 zoning  \
2     VRES1 - VACANT RESIDENTIAL 1            141149.0  R2 - RES - TWO FAMILY   
7     VRES1 - VACANT RESIDENTIAL 1              5997.0  R2 - RES - TWO FAMILY   
8     VRES1 - VACANT RESIDENTIAL 1              2399.0  R2 - RES - TWO FAMILY   
34    VRES1 - VACANT RESIDENTIAL 1              3475.0  R2 - RES - TWO FAMILY   
236   VRES1 - VACANT RESIDENTIAL 1             18092.0  R2 - RES - TWO FAMILY   
701   VRES1 - VACANT RESIDENTIAL 1              5250.0  R2 - RES - TWO FAMILY   
704   VRES1 - VACANT RESIDENTIAL 1              7125.

In [12]:
# After looking at the map, there are a handful of outliers that I don't want to get rid of.
# Instead, I'll start by clearing out the ones with no street number

df_clean = df[df.street_number.notnull()]

In [13]:
df_clean.shape

(2656, 19)

In [14]:
# I also want to remove schools, churches and gov buildings. The idea is to look at residences in the analysis. 
# I am still debating the inclusion of businesses, so I won't abandon them YET
# To get rid of these insitutional buildings, I want to look at the property_class.

df.property_class_1.unique()

array(['OTHER', 'INSTITUTIONAL', 'RESIDENTIAL 1', nan, 'RESIDENTIAL 2',
       'RESIDENTIAL 3'], dtype=object)

In [15]:
# Look at all 'Institutional' class properties
df[df['property_class_1'] == 'INSTITUTIONAL']

roll_number  street_number unit_number street_direction  street_name  \
1     12080240200         1420.0         NaN              NaN      PORTAGE   
293   12080611100          511.0         NaN              NaN      CLIFTON   
622   12081074500          533.0         NaN              NaN    GREENWOOD   
974   12081492000          292.0         NaN              NaN       AUBREY   
1286  12081881000          930.0         NaN              NaN      PORTAGE   
1384  12081995000          960.0         NaN              NaN     WOLSELEY   
1448  12082093000          236.0         NaN              NaN         RUBY   
1746  12082460000          141.0         NaN              NaN    ARLINGTON   
1862  12082596000          240.0         NaN              NaN         HOME   
1865  12082608100          870.0         NaN              NaN      PORTAGE   
1891  12082683000          160.0         NaN              NaN    ETHELBERT   
1981  12082797000          191.0         NaN              NaN    ETHELBERT   
2057  12082874000           61.0         NaN              NaN      PICARDY   
2064  12082899000          788.0         NaN              NaN     WOLSELEY   
2065  12082900100          784.0         NaN              NaN     WOLSELEY   
2137  12082978500           65.0         NaN              NaN       WALNUT   
2250  12083128100          790.0         NaN              NaN     HONEYMAN   
2311  12090018000          750.0         NaN              NaN     WOLSELEY   
2398  12090129600          228.0         NaN              NaN     MARYLAND   
2474  12090220000           36.0         NaN              NaN      ALLOWAY   
2506  12090259100          120.0         NaN              NaN     MARYLAND   
2507  12090260100          745.0         NaN              NaN  WESTMINSTER   
2628  12097750000           10.0         NaN              NaN      PICARDY   
2654  12097803960            3.0         NaN              NaN    BORROWMAN   

     street_type            full_address neighbourhood_area  \
1         AVENUE     1420 PORTAGE AVENUE           WOLSELEY   
293       STREET      511 CLIFTON STREET           WOLSELEY   
622        PLACE     533 GREENWOOD PLACE           WOLSELEY   
974       STREET       292 AUBREY STREET           WOLSELEY   
1286      AVENUE      930 PORTAGE AVENUE           WOLSELEY   
1384      AVENUE     960 WOLSELEY AVENUE           WOLSELEY   
1448      STREET         236 RUBY STREET           WOLSELEY   
1746      STREET    141 ARLINGTON STREET           WOLSELEY   
1862      STREET         240 HOME STREET           WOLSELEY   
1865      AVENUE      870 PORTAGE AVENUE           WOLSELEY   
1891      STREET    160 ETHELBERT STREET           WOLSELEY   
1981      STREET    191 ETHELBERT STREET           WOLSELEY   
2057       PLACE        61 PICARDY PLACE           WOLSELEY   
2064      AVENUE     788 WOLSELEY AVENUE           WOLSELEY   
2065      AVENUE     784 WOLSELEY AVENUE           WOLSELEY   
2137      STREET        65 WALNUT STREET           WOLSELEY   
2250      AVENUE     790 HONEYMAN AVENUE           WOLSELEY   
2311      AVENUE     750 WOLSELEY AVENUE           WOLSELEY   
2398      STREET     228 MARYLAND STREET           WOLSELEY   
2474      AVENUE       36 ALLOWAY AVENUE           WOLSELEY   
2506      STREET     120 MARYLAND STREET           WOLSELEY   
2507      AVENUE  745 WESTMINSTER AVENUE           WOLSELEY   
2628       PLACE        10 PICARDY PLACE           WOLSELEY   
2654       PLACE       3 BORROWMAN PLACE           WOLSELEY   

                   property_use_code  assessed_land_area  \
1                     PIICH - CHURCH             88446.0   
293                   PIISC - SCHOOL            142947.0   
622               RESAP - APARTMENTS             25625.0   
974   RESGC - RESIDENTIAL GROUP CARE              2916.0   
1286                  CMOFF - OFFICE             12001.0   
1384                  PIISC - SCHOOL            145582.0   
1448  RESGC - RESIDENTIAL GROUP CARE              3026.0   

In [16]:
# How many are there?
len(df[df['property_class_1'] == 'INSTITUTIONAL'])

24

In [17]:
# And what are the use codes?
df[df['property_class_1'] == 'INSTITUTIONAL'].property_use_code.unique()

array(['PIICH - CHURCH', 'PIISC - SCHOOL', 'RESAP - APARTMENTS',
       'RESGC - RESIDENTIAL GROUP CARE', 'CMOFF - OFFICE',
       'PIIDC - DAY CARE'], dtype=object)

In [18]:
# The residential apartment is a care home. I want to keep that for now. (I know it has a garden)
# Instead of cutting all he institutions, I'll go by use codes. Churches and schools can go.

df[(df['property_use_code']== 'PIICH - CHURCH') | (df['property_use_code'] == 'PIISC - SCHOOL')]

roll_number  street_number unit_number street_direction  street_name  \
1     12080240200         1420.0         NaN              NaN      PORTAGE   
293   12080611100          511.0         NaN              NaN      CLIFTON   
1384  12081995000          960.0         NaN              NaN     WOLSELEY   
1862  12082596000          240.0         NaN              NaN         HOME   
1891  12082683000          160.0         NaN              NaN    ETHELBERT   
2057  12082874000           61.0         NaN              NaN      PICARDY   
2065  12082900100          784.0         NaN              NaN     WOLSELEY   
2137  12082978500           65.0         NaN              NaN       WALNUT   
2250  12083128100          790.0         NaN              NaN     HONEYMAN   
2311  12090018000          750.0         NaN              NaN     WOLSELEY   
2507  12090260100          745.0         NaN              NaN  WESTMINSTER   
2654  12097803960            3.0         NaN              NaN    BORROWMAN   

     street_type            full_address neighbourhood_area property_use_code  \
1         AVENUE     1420 PORTAGE AVENUE           WOLSELEY    PIICH - CHURCH   
293       STREET      511 CLIFTON STREET           WOLSELEY    PIISC - SCHOOL   
1384      AVENUE     960 WOLSELEY AVENUE           WOLSELEY    PIISC - SCHOOL   
1862      STREET         240 HOME STREET           WOLSELEY    PIICH - CHURCH   
1891      STREET    160 ETHELBERT STREET           WOLSELEY    PIICH - CHURCH   
2057       PLACE        61 PICARDY PLACE           WOLSELEY    PIICH - CHURCH   
2065      AVENUE     784 WOLSELEY AVENUE           WOLSELEY    PIISC - SCHOOL   
2137      STREET        65 WALNUT STREET           WOLSELEY    PIICH - CHURCH   
2250      AVENUE     790 HONEYMAN AVENUE           WOLSELEY    PIICH - CHURCH   
2311      AVENUE     750 WOLSELEY AVENUE           WOLSELEY    PIISC - SCHOOL   
2507      AVENUE  745 WESTMINSTER AVENUE           WOLSELEY    PIICH - CHURCH   
2654       PLACE       3 BORROWMAN PLACE           WOLSELEY    PIISC - SCHOOL   

      assessed_land_area                     zoning  total_assessed_value  \
1                88446.0      R2 - RES - TWO FAMILY             3144000.0   
293             142947.0      R2 - RES - TWO FAMILY             4922000.0   
1384            145582.0      R2 - RES - TWO FAMILY            10953000.0   
1862              8233.0      R2 - RES - TWO FAMILY              699000.0   
1891             14440.0      R2 - RES - TWO FAMILY             1186000.0   
2057             17724.0      R2 - RES - TWO FAMILY             1458000.0   
2065             25961.0      R2 - RES - TWO FAMILY             2229000.0   
2137             21933.0      R2 - RES - TWO FAMILY             1571000.0   
2250             12176.0      R2 - RES - TWO FAMILY             1432000.0   
2311             85251.0      R2 - RES - TWO FAMILY             3879000.0   
2507             29839.0  RMFM - RES - MULTI-FAMILY             4510000.0   
2654            255269.0  RMFM - RES - MULTI-FAMILY            10369000.0   

             assessment_date  \
1     04/01/2023 12:00:00 AM   
293   04/01/2023 12:00:00 AM   
1384  04/01/2023 12:00:00 AM   
1862  04/01/2023 12:00:00 AM   
1891  04/01/2023 12:00:00 AM   
2057  04/01/2023 12:00:00 AM   
2065  04/01/2023 12:00:00 AM   
2137  04/01/2023 12:00:00 AM   
2250  04/01/2023 12:00:00 AM   
2311  04/01/2023 12:00:00 AM   
2507  04/01/2023 12:00:00 AM   
2654  04/01/2023 12:00:00 AM   

                                             detail_url  \
1     http://www.winnipegassessment.com/asmtpub/engl...   
293   http://www.winnipegassessment.com/asmtpub/engl...   
1384  http://www.winnipegassessment.com/asmtpub/engl...   
1862  http://www.winnipegassessment.com/asmtpub/engl...   
1891  http://www.winnipegassessment.com/asmtpub/engl...   
2057  http://www.winnipegassessment.com/asmtpub/engl...   
2065  http://www.winnipegassessment.com/asmtpub/engl...   
2137  http://www.winnipegassessment.com/asmtpu

In [19]:
len(df[(df['property_use_code']== 'PIICH - CHURCH') | (df['property_use_code'] == 'PIISC - SCHOOL')])

12

In [20]:
# First, gather the indexes
institutions = df_clean[(df_clean['property_use_code']== 'PIICH - CHURCH')|(df_clean['property_use_code'] == 'PIISC - SCHOOL')].index

In [21]:
# And drop them
df_clean = df_clean.drop(institutions, axis=0)

In [29]:
# Let's look at what's left...
df_clean.property_use_code.unique()

array(['RESSD - DETACHED SINGLE DWELLING', 'CMOFF - OFFICE',
       'CMRST - STORE', 'VRES1 - VACANT RESIDENTIAL 1',
       'RESMC - MULTIFAMILY CONVERSION',
       'RESSU - RESIDENTIAL SECONDARY UNIT',
       'RESMA - MULTIPLE ATTACHED UNITS', 'RESDU - DUPLEX',
       'CMFBK - BANK', 'CMRCV - CONVENIENCE STORE', 'CMRRE - RESTAURANT',
       'RESAP - APARTMENTS', 'CMSTP - STRIP MALL',
       'RESGC - RESIDENTIAL GROUP CARE',
       'RESMU - RESIDENTIAL MULTIPLE USE',
       'CMCMU - COMMERCIAL MULTIPLE USE', 'PIRCC - COMMUNITY CENTRE',
       'RESTR - TRIPLEX', 'CNCMP - CONDO COMPLEX',
       'CNRES - CONDO RESIDENTIAL', 'CMOMC - MEDICAL OFFICE CLINIC',
       'RESAM - APARTMENTS MULTIPLE USE',
       'PIIGC - NON-RESIDENTIAL GROUP CARE',
       'CMMRH - COMMERCIAL ROW HOUSE',
       'RESMB - RESIDENTIAL MULTIPLE BUILDINGS', 'PIIDC - DAY CARE',
       'RESSS - SIDE BY SIDE', 'RESRM - ROOMING HOUSE',
       'CNAPT - CONDO APARTMENT', 'CNCOM - CONDO COMMERCIAL'],
      dtype=object)

In [30]:
# Cool. I also don't need parks with buildings, garages (vehicle service), parking lots, government buildings...

df[df['property_use_code'].isin(['PIRPK - PARK WITH BUILDING','CMOGV - GOVERNMENT OFFICE','CMPSP - SURFACE PARKING','CMVSR - VEHICLE SERVICE RELATED'])]

roll_number  street_number unit_number street_direction street_name  \
0     12080201000         1430.0         NaN              NaN     PORTAGE   
205   12080494000         1284.0         NaN              NaN     PORTAGE   
475   12080900500         1150.0         NaN              NaN     PORTAGE   
1045  12081585000          329.0         NaN              NaN      AUBREY   
1046  12081586000          970.0         NaN              NaN     PORTAGE   
1868  12082620100          821.0         NaN              NaN     PRESTON   
2301  12083215100          800.0         NaN              NaN     PORTAGE   
2308  12090012100           20.0         NaN              NaN    MARYLAND   
2509  12090263100          712.0         NaN              NaN     PORTAGE   

     street_type         full_address neighbourhood_area  \
0         AVENUE  1430 PORTAGE AVENUE           WOLSELEY   
205       AVENUE  1284 PORTAGE AVENUE           WOLSELEY   
475       AVENUE  1150 PORTAGE AVENUE           WOLSELEY   
1045      STREET    329 AUBREY STREET           WOLSELEY   
1046      AVENUE   970 PORTAGE AVENUE           WOLSELEY   
1868      AVENUE   821 PRESTON AVENUE           WOLSELEY   
2301      AVENUE   800 PORTAGE AVENUE           WOLSELEY   
2308      STREET   20 MARYLAND STREET           WOLSELEY   
2509      AVENUE   712 PORTAGE AVENUE           WOLSELEY   

                    property_use_code  assessed_land_area  \
0          PIRPK - PARK WITH BUILDING            488220.0   
205   CMVSR - VEHICLE SERVICE RELATED             22077.0   
475   CMVSR - VEHICLE SERVICE RELATED             13854.0   
1045          CMPSP - SURFACE PARKING              2252.0   
1046  CMVSR - VEHICLE SERVICE RELATED             14710.0   
1868       PIRPK - PARK WITH BUILDING            260483.0   
2301        CMOGV - GOVERNMENT OFFICE             34646.0   
2308  CMVSR - VEHICLE SERVICE RELATED             12669.0   
2509  CMVSR - VEHICLE SERVICE RELATED             13821.0   

                      zoning  total_assessed_value         assessment_date  \
0     PR1 - PRKS&REC-PASSIVE             3130000.0  04/01/2023 12:00:00 AM   
205     C2 - COM - COMMUNITY             1304000.0  04/01/2023 12:00:00 AM   
475     C2 - COM - COMMUNITY             1041000.0  04/01/2023 12:00:00 AM   
1045    C2 - COM - COMMUNITY              101000.0  04/01/2023 12:00:00 AM   
1046    C2 - COM - COMMUNITY             1306000.0  04/01/2023 12:00:00 AM   
1868   R2 - RES - TWO FAMILY             7596000.0  04/01/2023 12:00:00 AM   
2301    C2 - COM - COMMUNITY             9226000.0  04/01/2023 12:00:00 AM   
2308    C2 - COM - COMMUNITY              874000.0  04/01/2023 12:00:00 AM   
2509    C2 - COM - COMMUNITY             1193000.0  04/01/2023 12:00:00 AM   

                                             detail_url  \
0     http://www.winnipegassessment.com/asmtpub/engl...   
205   http://www.winnipegassessment.com/asmtpub/engl...   
475   http://www.winnipegassessment.com/asmtpub/engl...   
1045  http://www.winnipegassessment.com/asmtpub/engl...   
1046  http://www.winnipegassessment.com/asmtpub/engl...   
1868  http://www.winnipegassessment.com/asmtpub/engl...   
2301  http://www.winnipegassessment.com/asmtpub/engl...   
2308  http://www.winnipegassessment.com/asmtpub/engl...   
2509  http://www.winnipegassessment.com/asmtpub/engl...   

      current_assessment_year property_class_1  \
0                        2026            OTHER   
205                      2026            OTHER   
475                      2026            OTHER   
1045                     2026            OTHER   
1046                     2026            OTHER   
1868                     2026            OTHER   
2301                     2026            OTHER   
2308                     2026            OTHER   
2509                     2026            OTHER   

                                               geometry  centroid_lat  \
0     MULTIPOLYGON (((-97.19095901066672 49.87922629...     49.879843   
205 

In [31]:
# This is a very fun learning process in terms of figuring out the most efficient ways to clean.
# Is in might have been useful from the start!

len(df[df['property_use_code'].isin(['PIRPK - PARK WITH BUILDING','CMOGV - GOVERNMENT OFFICE','CMPSP - SURFACE PARKING','CMVSR - VEHICLE SERVICE RELATED'])])

9

In [32]:
# Let's drop these 9

extras = df_clean[df_clean['property_use_code'].isin(['PIRPK - PARK WITH BUILDING','CMOGV - GOVERNMENT OFFICE','CMPSP - SURFACE PARKING','CMVSR - VEHICLE SERVICE RELATED'])].index
df_clean = df_clean.drop(extras, axis=0)

In [33]:
df_clean.shape

(2635, 19)

In [34]:
# We should now be left with business and residential properties. Let's look!
df_clean.property_use_code.unique()

array(['RESSD - DETACHED SINGLE DWELLING', 'CMOFF - OFFICE',
       'CMRST - STORE', 'VRES1 - VACANT RESIDENTIAL 1',
       'RESMC - MULTIFAMILY CONVERSION',
       'RESSU - RESIDENTIAL SECONDARY UNIT',
       'RESMA - MULTIPLE ATTACHED UNITS', 'RESDU - DUPLEX',
       'CMFBK - BANK', 'CMRCV - CONVENIENCE STORE', 'CMRRE - RESTAURANT',
       'RESAP - APARTMENTS', 'CMSTP - STRIP MALL',
       'RESGC - RESIDENTIAL GROUP CARE',
       'RESMU - RESIDENTIAL MULTIPLE USE',
       'CMCMU - COMMERCIAL MULTIPLE USE', 'PIRCC - COMMUNITY CENTRE',
       'RESTR - TRIPLEX', 'CNCMP - CONDO COMPLEX',
       'CNRES - CONDO RESIDENTIAL', 'CMOMC - MEDICAL OFFICE CLINIC',
       'RESAM - APARTMENTS MULTIPLE USE',
       'PIIGC - NON-RESIDENTIAL GROUP CARE',
       'CMMRH - COMMERCIAL ROW HOUSE',
       'RESMB - RESIDENTIAL MULTIPLE BUILDINGS', 'PIIDC - DAY CARE',
       'RESSS - SIDE BY SIDE', 'RESRM - ROOMING HOUSE',
       'CNAPT - CONDO APARTMENT', 'CNCOM - CONDO COMMERCIAL'],
      dtype=object)

In [35]:
# First I'm going to split off the businesses and other non-residential properties(i.e. the community centre and daycare). 

non_residential = df_clean[df_clean['property_use_code'].isin([
    'CMOFF - OFFICE','CMRST - STORE','CMFBK - BANK','CMRCV - CONVENIENCE STORE', 
    'CMRRE - RESTAURANT','CMSTP - STRIP MALL','CMCMU - COMMERCIAL MULTIPLE USE', 
    'PIRCC - COMMUNITY CENTRE','CMOMC - MEDICAL OFFICE CLINIC', 'PIIGC - NON-RESIDENTIAL GROUP CARE',
       'CMMRH - COMMERCIAL ROW HOUSE', 'PIIDC - DAY CARE','CNCOM - CONDO COMMERCIAL'])]

In [36]:
non_residential.head(20)

roll_number  street_number unit_number street_direction street_name  \
11   12080268100         1412.0         NaN              NaN     PORTAGE   
28   12080293000         1308.0         NaN              NaN     PORTAGE   
29   12080295000         1314.0         NaN              NaN     PORTAGE   
30   12080296100         1318.0         NaN              NaN     PORTAGE   
31   12080297100         1320.0         NaN              NaN     PORTAGE   
32   12080298000         1324.0         NaN              NaN     PORTAGE   
33   12080300000         1330.0         NaN              NaN     PORTAGE   
172  12080456200         1300.0         NaN              NaN     PORTAGE   
206  12080500000          545.0         NaN                S      TELFER   
280  12080595000         1250.0         NaN              NaN     PORTAGE   
294  12080640500         1240.0         NaN              NaN     PORTAGE   
352  12080715100         1200.0         NaN              NaN     PORTAGE   
403  12080804000         1184.0         NaN              NaN     PORTAGE   
510  12080940000         1146.0         NaN              NaN     PORTAGE   
540  12080973000         1140.0         NaN              NaN     PORTAGE   
541  12080975000         1132.0         NaN              NaN     PORTAGE   
542  12080993000         1098.0         NaN              NaN     PORTAGE   
543  12080994000         1110.0         NaN              NaN     PORTAGE   
544  12080995000         1114.0         NaN              NaN     PORTAGE   
664  12081133200         1080.0         NaN              NaN     PORTAGE   

    street_type         full_address neighbourhood_area  \
11       AVENUE  1412 PORTAGE AVENUE           WOLSELEY   
28       AVENUE  1308 PORTAGE AVENUE           WOLSELEY   
29       AVENUE  1314 PORTAGE AVENUE           WOLSELEY   
30       AVENUE  1318 PORTAGE AVENUE           WOLSELEY   
31       AVENUE  1320 PORTAGE AVENUE           WOLSELEY   
32       AVENUE  1324 PORTAGE AVENUE           WOLSELEY   
33       AVENUE  1330 PORTAGE AVENUE           WOLSELEY   
172      AVENUE  1300 PORTAGE AVENUE           WOLSELEY   
206      STREET  545 TELFER STREET S           WOLSELEY   
280      AVENUE  1250 PORTAGE AVENUE           WOLSELEY   
294      AVENUE  1240 PORTAGE AVENUE           WOLSELEY   
352      AVENUE  1200 PORTAGE AVENUE           WOLSELEY   
403      AVENUE  1184 PORTAGE AVENUE           WOLSELEY   
510      AVENUE  1146 PORTAGE AVENUE           WOLSELEY   
540      AVENUE  1140 PORTAGE AVENUE           WOLSELEY   
541      AVENUE  1132 PORTAGE AVENUE           WOLSELEY   
542      AVENUE  1098 PORTAGE AVENUE           WOLSELEY   
543      AVENUE  1110 PORTAGE AVENUE           WOLSELEY   
544      AVENUE  1114 PORTAGE AVENUE           WOLSELEY   
664      AVENUE  1080 PORTAGE AVENUE           WOLSELEY   

             property_use_code  assessed_land_area                 zoning  \
11              CMOFF - OFFICE             13115.0   C2 - COM - COMMUNITY   
28               CMRST - STORE              6114.0   C2 - COM - COMMUNITY   
29               CMRST - STORE              2902.0   C2 - COM - COMMUNITY   
30               CMRST - STORE              2318.0   C2 - COM - COMMUNITY   
31               CMRST - STORE              3692.0   C2 - COM - COMMUNITY   
32               CMRST - STORE              6011.0   C2 - COM - COMMUNITY   
33               CMRST - STORE             17473.0   C2 - COM - COMMUNITY   
172              CMRST - STORE             23696.0   C2 - COM - COMMUNITY   
206              CMRST - STORE              4055.0  R2 - RES - TWO FAMILY   
280               CMFBK - BANK             12274.0   C2 - COM - COMMUNITY   
294             CMOFF - OFFICE             30747.0   C2 - COM - COMMUNITY   
352             CMOFF - OFFICE             22479.0   C2 - COM - COMMUNITY   
403  CMRCV - CONVENIENCE STORE             24182.0   C2 - COM - COMMUNITY   
510         CMRRE - RESTAURANT             13114.0   C2 - COM - COMMUNITY   
540          

In [37]:
# I'm going to list all rows because I want to double check any that I don't feel confident about

pd.set_option('display.max_rows', None)
non_residential

roll_number  street_number unit_number street_direction  street_name  \
11    12080268100         1412.0         NaN              NaN      PORTAGE   
28    12080293000         1308.0         NaN              NaN      PORTAGE   
29    12080295000         1314.0         NaN              NaN      PORTAGE   
30    12080296100         1318.0         NaN              NaN      PORTAGE   
31    12080297100         1320.0         NaN              NaN      PORTAGE   
32    12080298000         1324.0         NaN              NaN      PORTAGE   
33    12080300000         1330.0         NaN              NaN      PORTAGE   
172   12080456200         1300.0         NaN              NaN      PORTAGE   
206   12080500000          545.0         NaN                S       TELFER   
280   12080595000         1250.0         NaN              NaN      PORTAGE   
294   12080640500         1240.0         NaN              NaN      PORTAGE   
352   12080715100         1200.0         NaN              NaN      PORTAGE   
403   12080804000         1184.0         NaN              NaN      PORTAGE   
510   12080940000         1146.0         NaN              NaN      PORTAGE   
540   12080973000         1140.0         NaN              NaN      PORTAGE   
541   12080975000         1132.0         NaN              NaN      PORTAGE   
542   12080993000         1098.0         NaN              NaN      PORTAGE   
543   12080994000         1110.0         NaN              NaN      PORTAGE   
544   12080995000         1114.0         NaN              NaN      PORTAGE   
664   12081133200         1080.0         NaN              NaN      PORTAGE   
694   12081164100         1054.0         NaN              NaN      PORTAGE   
889   12081389000         1046.0         NaN              NaN      PORTAGE   
890   12081392100         1038.0         NaN              NaN      PORTAGE   
891   12081393100         1036.0         NaN              NaN      PORTAGE   
892   12081394100         1032.0         NaN              NaN      PORTAGE   
984   12081503300          980.0         NaN              NaN      PORTAGE   
1093  12081639000          960.0         NaN              NaN  WESTMINSTER   
1094  12081642000          966.0         NaN              NaN      PORTAGE   
1095  12081643000          960.0         NaN              NaN      PORTAGE   
1096  12081645500          956.0         NaN              NaN      PORTAGE   
1097  12081647000          950.0         NaN              NaN      PORTAGE   
1195  12081769200          980.0         NaN              NaN   PALMERSTON   
1279  12081865000          912.0         NaN              NaN      PORTAGE   
1285  12081878000          934.0         NaN              NaN      PORTAGE   
1286  12081881000          930.0         NaN              NaN      PORTAGE   
1337  12081945000          965.0         NaN              NaN     WOLSELEY   
1359  12081967000          894.0         NaN              NaN  WESTMINSTER   
1360  12081968000          898.0         NaN              NaN  WESTMINSTER   
1361  12081969500          900.0         NaN              NaN  WESTMINSTER   
1456  12082101000          938.0         NaN              NaN      PORTAGE   
1604  12082284000          146.0         NaN              NaN    ARLINGTON   
1606  12082286000          869.0         NaN              NaN  WESTMINSTER   
1618  12082300000          210.0         NaN              NaN      EVANSON   
1641  12082330000          250.0         NaN              NaN      EVANSON   
1642  12082333500          888.0         NaN              NaN      PORTAGE   
1643  12082334500          894.0         NaN              NaN      PORTAGE   
1644  12082337000          904.0         NaN              NaN      PORTAGE   
1746  12082460000          141.0         NaN              NaN    ARLINGTON   
1864  12082604100          880.0         NaN              NaN      PORTAGE   
1865  12082608100          870.0         NaN              NaN      PORTAGE   
2061  12082893500          8

In [40]:
pd.reset_option('display.max_rows')

In [41]:
# After reviewing these addresses on the map, I'm going to keep the rowhouses, and the rest can be trimmed from the residential data
non_residential = df_clean[df_clean['property_use_code'].isin([
    'CMOFF - OFFICE','CMRST - STORE','CMFBK - BANK','CMRCV - CONVENIENCE STORE', 
    'CMRRE - RESTAURANT','CMSTP - STRIP MALL','CMCMU - COMMERCIAL MULTIPLE USE', 
    'PIRCC - COMMUNITY CENTRE','CMOMC - MEDICAL OFFICE CLINIC', 'PIIGC - NON-RESIDENTIAL GROUP CARE',
    'PIIDC - DAY CARE','CNCOM - CONDO COMMERCIAL'])]

In [42]:
non_residential.index

Index([  11,   28,   29,   30,   31,   32,   33,  172,  206,  280,  294,  352,
        403,  510,  540,  541,  542,  543,  544,  664,  694,  889,  890,  891,
        892,  984, 1093, 1094, 1095, 1096, 1097, 1195, 1279, 1285, 1286, 1337,
       1359, 1360, 1361, 1456, 1604, 1606, 1618, 1642, 1643, 1644, 1746, 1864,
       1865, 2163, 2164, 2165, 2318, 2398, 2418, 2506, 2508, 2519, 2520, 2524,
       2659],
      dtype='int64')

In [43]:
residential = df_clean.drop(non_residential.index, axis=0)

In [44]:
residential

roll_number  street_number unit_number street_direction street_name  \
3     12080260000          542.0         NaN              NaN      RAGLAN   
4     12080261000          538.0         NaN              NaN      RAGLAN   
5     12080262000          528.0         NaN              NaN      RAGLAN   
6     12080263000          522.0         NaN              NaN      RAGLAN   
9     12080265000         1338.0         NaN              NaN    WOLSELEY   
...           ...            ...         ...              ...         ...   
2666  12097805100           54.0         401              NaN    MARYLAND   
2667  12097805105           54.0         402              NaN    MARYLAND   
2668  12097806720          205.0         NaN              NaN   ARLINGTON   
2669  12097809455          510.0         NaN              NaN      NEWMAN   
2670  12097809460          518.0         NaN              NaN      NEWMAN   

     street_type            full_address neighbourhood_area  \
3           ROAD         542 RAGLAN ROAD           WOLSELEY   
4           ROAD         538 RAGLAN ROAD           WOLSELEY   
5           ROAD         528 RAGLAN ROAD           WOLSELEY   
6           ROAD         522 RAGLAN ROAD           WOLSELEY   
9         AVENUE    1338 WOLSELEY AVENUE           WOLSELEY   
...          ...                     ...                ...   
2666      STREET  401-54 MARYLAND STREET           WOLSELEY   
2667      STREET  402-54 MARYLAND STREET           WOLSELEY   
2668      STREET    205 ARLINGTON STREET           WOLSELEY   
2669      STREET       510 NEWMAN STREET           WOLSELEY   
2670      STREET       518 NEWMAN STREET           WOLSELEY   

                     property_use_code  assessed_land_area  \
3     RESSD - DETACHED SINGLE DWELLING              5997.0   
4     RESSD - DETACHED SINGLE DWELLING              5997.0   
5     RESSD - DETACHED SINGLE DWELLING              5997.0   
6     RESSD - DETACHED SINGLE DWELLING              5997.0   
9     RESSD - DETACHED SINGLE DWELLING             18720.0   
...                                ...                 ...   
2666           CNAPT - CONDO APARTMENT                 NaN   
2667           CNAPT - CONDO APARTMENT                 NaN   
2668                RESAP - APARTMENTS             10643.0   
2669  RESSD - DETACHED SINGLE DWELLING              2863.0   
2670  RESSD - DETACHED SINGLE DWELLING              5022.0   

                     zoning  total_assessed_value         assessment_date  \
3     R2 - RES - TWO FAMILY              305000.0  04/01/2023 12:00:00 AM   
4     R2 - RES - TWO FAMILY              364000.0  04/01/2023 12:00:00 AM   
5     R2 - RES - TWO FAMILY              386000.0  04/01/2023 12:00:00 AM   
6     R2 - RES - TWO FAMILY              376000.0  04/01/2023 12:00:00 AM   
9     R2 - RES - TWO FAMILY             1385000.0  04/01/2023 12:00:00 AM   
...                     ...                   ...                     ...   
2666                    NaN              237000.0  04/01/2023 12:00:00 AM   
2667                    NaN              225000.0  04/01/2023 12:00:00 AM   
2668  R2 - RES - TWO FAMILY             1445000.0  04/01/2023 12:00:00 AM   
2669  R2 - RES - TWO FAMILY              469000.0  04/01/2023 12:00:00 AM   
2670  R2 - RES - TWO FAMILY              466000.0  04/01/2023 12:00:00 AM   

                                             detail_url  \
3     http://www.winnipegassessment.com/AsmtPub/engl...   
4     http://www.winnipegassessment.com/AsmtPub/engl...   
5     http://www.winnipegassessment.com/AsmtPub/engl...   
6     http://www.winnipegassessment.com/AsmtPub/engl...   
9     http://www.winnipegassessment.com/AsmtPub/engl...   
...                                                 ...   
2666  http://www.winnipegassessment.com/AsmtPub/engl...   
2667  http://www.winnipegassessment.com/AsmtPub/engl...   
2668  http://www.winnipegassessment.com/asmtpub/engl...   
2669  http://www.winnipegassessment.com/AsmtPub/engl...   
2670 

In [45]:
# Nice! I now have a dataframe with only the residential buildings in Wolseley! 
residential.property_use_code.unique()

array(['RESSD - DETACHED SINGLE DWELLING', 'VRES1 - VACANT RESIDENTIAL 1',
       'RESMC - MULTIFAMILY CONVERSION',
       'RESSU - RESIDENTIAL SECONDARY UNIT',
       'RESMA - MULTIPLE ATTACHED UNITS', 'RESDU - DUPLEX',
       'RESAP - APARTMENTS', 'RESGC - RESIDENTIAL GROUP CARE',
       'RESMU - RESIDENTIAL MULTIPLE USE', 'RESTR - TRIPLEX',
       'CNCMP - CONDO COMPLEX', 'CNRES - CONDO RESIDENTIAL',
       'RESAM - APARTMENTS MULTIPLE USE', 'CMMRH - COMMERCIAL ROW HOUSE',
       'RESMB - RESIDENTIAL MULTIPLE BUILDINGS', 'RESSS - SIDE BY SIDE',
       'RESRM - ROOMING HOUSE', 'CNAPT - CONDO APARTMENT'], dtype=object)

In [46]:
# What's left in the vacant properties?

residential[residential['property_use_code']=='VRES1 - VACANT RESIDENTIAL 1']

roll_number  street_number unit_number street_direction  street_name  \
34    12080305500          534.0         NaN              NaN        CRAIG   
236   12080530000         1270.0         NaN              NaN     WOLSELEY   
701   12081184000         1064.0         NaN              NaN   PALMERSTON   
704   12081189100          104.0         NaN                S     GARFIELD   
919   12081435000         1020.0         NaN              NaN   PALMERSTON   
989   12081510000           35.0         NaN              NaN       AUBREY   
990   12081519200          139.0         NaN              NaN       AUBREY   
1222  12081806000           49.0         NaN              NaN       LENORE   
1223  12081807000           55.0         NaN              NaN       LENORE   
1596  12082275000          165.0         NaN              NaN      EVANSON   
1915  12082721100          850.0         NaN              NaN   PALMERSTON   
1968  12082784000          852.0         NaN              NaN  WESTMINSTER   
2462  12090208000           17.0         NaN              NaN      ALLOWAY   
2523  12097511500          547.0           1              NaN       NEWMAN   

     street_type            full_address neighbourhood_area  \
34        STREET        534 CRAIG STREET           WOLSELEY   
236       AVENUE    1270 WOLSELEY AVENUE           WOLSELEY   
701       AVENUE  1064 PALMERSTON AVENUE           WOLSELEY   
704       STREET   104 GARFIELD STREET S           WOLSELEY   
919       AVENUE  1020 PALMERSTON AVENUE           WOLSELEY   
989       STREET        35 AUBREY STREET           WOLSELEY   
990       STREET       139 AUBREY STREET           WOLSELEY   
1222      STREET        49 LENORE STREET           WOLSELEY   
1223      STREET        55 LENORE STREET           WOLSELEY   
1596      STREET      165 EVANSON STREET           WOLSELEY   
1915      AVENUE   850 PALMERSTON AVENUE           WOLSELEY   
1968      AVENUE  852 WESTMINSTER AVENUE           WOLSELEY   
2462      AVENUE       17 ALLOWAY AVENUE           WOLSELEY   
2523      STREET     1-547 NEWMAN STREET           WOLSELEY   

                 property_use_code  assessed_land_area                 zoning  \
34    VRES1 - VACANT RESIDENTIAL 1              3475.0  R2 - RES - TWO FAMILY   
236   VRES1 - VACANT RESIDENTIAL 1             18092.0  R2 - RES - TWO FAMILY   
701   VRES1 - VACANT RESIDENTIAL 1              5250.0  R2 - RES - TWO FAMILY   
704   VRES1 - VACANT RESIDENTIAL 1              7125.0  R2 - RES - TWO FAMILY   
919   VRES1 - VACANT RESIDENTIAL 1              4255.0  R2 - RES - TWO FAMILY   
989   VRES1 - VACANT RESIDENTIAL 1             25799.0  R2 - RES - TWO FAMILY   
990   VRES1 - VACANT RESIDENTIAL 1             16324.0  R2 - RES - TWO FAMILY   
1222  VRES1 - VACANT RESIDENTIAL 1              3051.0  R2 - RES - TWO FAMILY   
1223  VRES1 - VACANT RESIDENTIAL 1              6101.0  R2 - RES - TWO FAMILY   
1596  VRES1 - VACANT RESIDENTIAL 1              2444.0  R2 - RES - TWO FAMILY   
1915  VRES1 - VACANT RESIDENTIAL 1              5400.0  R2 - RES - TWO FAMILY   
1968  VRES1 - VACANT RESIDENTIAL 1              4405.0  R2 - RES - TWO FAMILY   
2462  VRES1 - VACANT RESIDENTIAL 1              3053.0  R2 - RES - TWO FAMILY   
2523  VRES1 - VACANT RESIDENTIAL 1              3710.0  R2 - RES - TWO FAMILY   

      total_assessed_value         assessment_date  \
34                214000.0  04/01/2023 12:00:00 AM   
236               522000.0  04/01/2023 12:00:00 AM   
701               442000.0  04/01/2023 12:00:00 AM   
704               438000.0  04/01/2023 12:00:00 AM   
919               430000.0  04/01/2023 12:00:00 AM   
989               400000.0  04/01/2023 12:00:00 AM   
990               369000.0  04/01/2023 12:00:00 AM   
1222              222000.0  04/01/2023 12:00:00 AM   
1223              250000.0  04/01/2023 12:00:00 AM   
1596              231000.0  04/01/2023 12:00:00 AM   
1915              443000.0  04/01/2023 12:00:00 AM   
1968              223000.

In [47]:
# Here's something I don't understand about the city data...
# SEVERAL on this list are parks! And yet they have the use code 'VRES', they're zoned R2, and they have a class of residential 1. 
# Maybe a question for the data people...

# But in the meantime, there aren't very many so I'm doing this manually. 
# I am going to drop any rows that refer to a genuinely vacant property, based on cross referencing to maps.

vacants_index = [34, 236, 919, 989, 990, 1222, 1223, 1596, 1915, 1968, 2462]
residential = residential.drop(vacants_index, axis=0)

In [48]:
# Amazing! Residential is real! 

residential

roll_number  street_number unit_number street_direction street_name  \
3     12080260000          542.0         NaN              NaN      RAGLAN   
4     12080261000          538.0         NaN              NaN      RAGLAN   
5     12080262000          528.0         NaN              NaN      RAGLAN   
6     12080263000          522.0         NaN              NaN      RAGLAN   
9     12080265000         1338.0         NaN              NaN    WOLSELEY   
...           ...            ...         ...              ...         ...   
2666  12097805100           54.0         401              NaN    MARYLAND   
2667  12097805105           54.0         402              NaN    MARYLAND   
2668  12097806720          205.0         NaN              NaN   ARLINGTON   
2669  12097809455          510.0         NaN              NaN      NEWMAN   
2670  12097809460          518.0         NaN              NaN      NEWMAN   

     street_type            full_address neighbourhood_area  \
3           ROAD         542 RAGLAN ROAD           WOLSELEY   
4           ROAD         538 RAGLAN ROAD           WOLSELEY   
5           ROAD         528 RAGLAN ROAD           WOLSELEY   
6           ROAD         522 RAGLAN ROAD           WOLSELEY   
9         AVENUE    1338 WOLSELEY AVENUE           WOLSELEY   
...          ...                     ...                ...   
2666      STREET  401-54 MARYLAND STREET           WOLSELEY   
2667      STREET  402-54 MARYLAND STREET           WOLSELEY   
2668      STREET    205 ARLINGTON STREET           WOLSELEY   
2669      STREET       510 NEWMAN STREET           WOLSELEY   
2670      STREET       518 NEWMAN STREET           WOLSELEY   

                     property_use_code  assessed_land_area  \
3     RESSD - DETACHED SINGLE DWELLING              5997.0   
4     RESSD - DETACHED SINGLE DWELLING              5997.0   
5     RESSD - DETACHED SINGLE DWELLING              5997.0   
6     RESSD - DETACHED SINGLE DWELLING              5997.0   
9     RESSD - DETACHED SINGLE DWELLING             18720.0   
...                                ...                 ...   
2666           CNAPT - CONDO APARTMENT                 NaN   
2667           CNAPT - CONDO APARTMENT                 NaN   
2668                RESAP - APARTMENTS             10643.0   
2669  RESSD - DETACHED SINGLE DWELLING              2863.0   
2670  RESSD - DETACHED SINGLE DWELLING              5022.0   

                     zoning  total_assessed_value         assessment_date  \
3     R2 - RES - TWO FAMILY              305000.0  04/01/2023 12:00:00 AM   
4     R2 - RES - TWO FAMILY              364000.0  04/01/2023 12:00:00 AM   
5     R2 - RES - TWO FAMILY              386000.0  04/01/2023 12:00:00 AM   
6     R2 - RES - TWO FAMILY              376000.0  04/01/2023 12:00:00 AM   
9     R2 - RES - TWO FAMILY             1385000.0  04/01/2023 12:00:00 AM   
...                     ...                   ...                     ...   
2666                    NaN              237000.0  04/01/2023 12:00:00 AM   
2667                    NaN              225000.0  04/01/2023 12:00:00 AM   
2668  R2 - RES - TWO FAMILY             1445000.0  04/01/2023 12:00:00 AM   
2669  R2 - RES - TWO FAMILY              469000.0  04/01/2023 12:00:00 AM   
2670  R2 - RES - TWO FAMILY              466000.0  04/01/2023 12:00:00 AM   

                                             detail_url  \
3     http://www.winnipegassessment.com/AsmtPub/engl...   
4     http://www.winnipegassessment.com/AsmtPub/engl...   
5     http://www.winnipegassessment.com/AsmtPub/engl...   
6     http://www.winnipegassessment.com/AsmtPub/engl...   
9     http://www.winnipegassessment.com/AsmtPub/engl...   
...                                                 ...   
2666  http://www.winnipegassessment.com/AsmtPub/engl...   
2667  http://www.winnipegassessment.com/AsmtPub/engl...   
2668  http://www.winnipegassessment.com/asmtpub/engl...   
2669  http://www.winnipegassessment.com/AsmtPub/engl...   
2670 

In [49]:
# Dealing with condos/apartments feels more complex. I will maybe have to come back to that.

In [50]:
# First... going cylcing to collect more garden data! Bye!

In [51]:
# Cleaning cont...
# I want to make this even smaller by getting rid of a few more columns

residential.columns

Index(['roll_number', 'street_number', 'unit_number', 'street_direction',
       'street_name', 'street_type', 'full_address', 'neighbourhood_area',
       'property_use_code', 'assessed_land_area', 'zoning',
       'total_assessed_value', 'assessment_date', 'detail_url',
       'current_assessment_year', 'property_class_1', 'geometry',
       'centroid_lat', 'centroid_lon'],
      dtype='object')

In [52]:
residential = residential[['roll_number', 'street_number', 'unit_number','street_name', 'street_type', 'full_address','property_use_code', 'assessed_land_area', 'zoning', 'total_assessed_value','property_class_1', 'geometry', 'centroid_lat', 'centroid_lon']]

In [53]:
residential

roll_number  street_number unit_number street_name street_type  \
3     12080260000          542.0         NaN      RAGLAN        ROAD   
4     12080261000          538.0         NaN      RAGLAN        ROAD   
5     12080262000          528.0         NaN      RAGLAN        ROAD   
6     12080263000          522.0         NaN      RAGLAN        ROAD   
9     12080265000         1338.0         NaN    WOLSELEY      AVENUE   
...           ...            ...         ...         ...         ...   
2666  12097805100           54.0         401    MARYLAND      STREET   
2667  12097805105           54.0         402    MARYLAND      STREET   
2668  12097806720          205.0         NaN   ARLINGTON      STREET   
2669  12097809455          510.0         NaN      NEWMAN      STREET   
2670  12097809460          518.0         NaN      NEWMAN      STREET   

                full_address                 property_use_code  \
3            542 RAGLAN ROAD  RESSD - DETACHED SINGLE DWELLING   
4            538 RAGLAN ROAD  RESSD - DETACHED SINGLE DWELLING   
5            528 RAGLAN ROAD  RESSD - DETACHED SINGLE DWELLING   
6            522 RAGLAN ROAD  RESSD - DETACHED SINGLE DWELLING   
9       1338 WOLSELEY AVENUE  RESSD - DETACHED SINGLE DWELLING   
...                      ...                               ...   
2666  401-54 MARYLAND STREET           CNAPT - CONDO APARTMENT   
2667  402-54 MARYLAND STREET           CNAPT - CONDO APARTMENT   
2668    205 ARLINGTON STREET                RESAP - APARTMENTS   
2669       510 NEWMAN STREET  RESSD - DETACHED SINGLE DWELLING   
2670       518 NEWMAN STREET  RESSD - DETACHED SINGLE DWELLING   

      assessed_land_area                 zoning  total_assessed_value  \
3                 5997.0  R2 - RES - TWO FAMILY              305000.0   
4                 5997.0  R2 - RES - TWO FAMILY              364000.0   
5                 5997.0  R2 - RES - TWO FAMILY              386000.0   
6                 5997.0  R2 - RES - TWO FAMILY              376000.0   
9                18720.0  R2 - RES - TWO FAMILY             1385000.0   
...                  ...                    ...                   ...   
2666                 NaN                    NaN              237000.0   
2667                 NaN                    NaN              225000.0   
2668             10643.0  R2 - RES - TWO FAMILY             1445000.0   
2669              2863.0  R2 - RES - TWO FAMILY              469000.0   
2670              5022.0  R2 - RES - TWO FAMILY              466000.0   

     property_class_1                                           geometry  \
3       RESIDENTIAL 1  MULTIPOLYGON (((-97.19102616382078 49.88138204...   
4       RESIDENTIAL 1  MULTIPOLYGON (((-97.19102616382078 49.88138204...   
5       RESIDENTIAL 1  MULTIPOLYGON (((-97.19104728492096 49.88110837...   
6       RESIDENTIAL 1  MULTIPOLYGON (((-97.19105784468728 49.88097154...   
9       RESIDENTIAL 1  MULTIPOLYGON (((-97.19051852774297 49.87921209...   
...               ...                                                ...   
2666    RESIDENTIAL 3  MULTIPOLYGON (((-97.16161542279819 49.88054499...   
2667    RESIDENTIAL 3  MULTIPOLYGON (((-97.16161542279819 49.88054499...   
2668    RESIDENTIAL 2  MULTIPOLYGON (((-97.16939763322243 49.88371190...   
2669    RESIDENTIAL 1  MULTIPOLYGON (((-97.18414267002349 49.88215925...   
2670    RESIDENTIAL 1  MULTIPOLYGON (((-97.18413124211199 49.88230564...   

      centroid_lat  centroid_lon  
3        49.881459    -97.191275  
4        49.881322    -97.191286  
5        49.881185    -97.191296  
6        49.881048    -97.191307  
9        49.878845    -97.190766  
...            ...           ...  
2666     49.880481    -97.161407  
2667     49.880481    -97.161407  
2668     49.883560    -97.169196  
2669     49.882111    -97.183947  
2670     49.882226    -97.183938  

[2563 rows x 14 columns]

In [54]:
residential.to_csv("wolseley_residential.csv",encoding='utf-8')

### CORRECTION:

I'm realizing I don't want to strip all the commercial properties. I'm going back to the df_clean dataframe (which still includes just businesses and residental) to clean up some vacant properties and work from there, ignoring residential.

In [55]:
df_clean

roll_number  street_number unit_number street_direction street_name  \
3     12080260000          542.0         NaN              NaN      RAGLAN   
4     12080261000          538.0         NaN              NaN      RAGLAN   
5     12080262000          528.0         NaN              NaN      RAGLAN   
6     12080263000          522.0         NaN              NaN      RAGLAN   
9     12080265000         1338.0         NaN              NaN    WOLSELEY   
...           ...            ...         ...              ...         ...   
2666  12097805100           54.0         401              NaN    MARYLAND   
2667  12097805105           54.0         402              NaN    MARYLAND   
2668  12097806720          205.0         NaN              NaN   ARLINGTON   
2669  12097809455          510.0         NaN              NaN      NEWMAN   
2670  12097809460          518.0         NaN              NaN      NEWMAN   

     street_type            full_address neighbourhood_area  \
3           ROAD         542 RAGLAN ROAD           WOLSELEY   
4           ROAD         538 RAGLAN ROAD           WOLSELEY   
5           ROAD         528 RAGLAN ROAD           WOLSELEY   
6           ROAD         522 RAGLAN ROAD           WOLSELEY   
9         AVENUE    1338 WOLSELEY AVENUE           WOLSELEY   
...          ...                     ...                ...   
2666      STREET  401-54 MARYLAND STREET           WOLSELEY   
2667      STREET  402-54 MARYLAND STREET           WOLSELEY   
2668      STREET    205 ARLINGTON STREET           WOLSELEY   
2669      STREET       510 NEWMAN STREET           WOLSELEY   
2670      STREET       518 NEWMAN STREET           WOLSELEY   

                     property_use_code  assessed_land_area  \
3     RESSD - DETACHED SINGLE DWELLING              5997.0   
4     RESSD - DETACHED SINGLE DWELLING              5997.0   
5     RESSD - DETACHED SINGLE DWELLING              5997.0   
6     RESSD - DETACHED SINGLE DWELLING              5997.0   
9     RESSD - DETACHED SINGLE DWELLING             18720.0   
...                                ...                 ...   
2666           CNAPT - CONDO APARTMENT                 NaN   
2667           CNAPT - CONDO APARTMENT                 NaN   
2668                RESAP - APARTMENTS             10643.0   
2669  RESSD - DETACHED SINGLE DWELLING              2863.0   
2670  RESSD - DETACHED SINGLE DWELLING              5022.0   

                     zoning  total_assessed_value         assessment_date  \
3     R2 - RES - TWO FAMILY              305000.0  04/01/2023 12:00:00 AM   
4     R2 - RES - TWO FAMILY              364000.0  04/01/2023 12:00:00 AM   
5     R2 - RES - TWO FAMILY              386000.0  04/01/2023 12:00:00 AM   
6     R2 - RES - TWO FAMILY              376000.0  04/01/2023 12:00:00 AM   
9     R2 - RES - TWO FAMILY             1385000.0  04/01/2023 12:00:00 AM   
...                     ...                   ...                     ...   
2666                    NaN              237000.0  04/01/2023 12:00:00 AM   
2667                    NaN              225000.0  04/01/2023 12:00:00 AM   
2668  R2 - RES - TWO FAMILY             1445000.0  04/01/2023 12:00:00 AM   
2669  R2 - RES - TWO FAMILY              469000.0  04/01/2023 12:00:00 AM   
2670  R2 - RES - TWO FAMILY              466000.0  04/01/2023 12:00:00 AM   

                                             detail_url  \
3     http://www.winnipegassessment.com/AsmtPub/engl...   
4     http://www.winnipegassessment.com/AsmtPub/engl...   
5     http://www.winnipegassessment.com/AsmtPub/engl...   
6     http://www.winnipegassessment.com/AsmtPub/engl...   
9     http://www.winnipegassessment.com/AsmtPub/engl...   
...                                                 ...   
2666  http://www.winnipegassessment.com/AsmtPub/engl...   
2667  http://www.winnipegassessment.com/AsmtPub/engl...   
2668  http://www.winnipegassessment.com/asmtpub/engl...   
2669  http://www.winnipegassessment.com/AsmtPub/engl...   
2670 

In [56]:
# Filtering to look at vacant residential and ensure the index remains the same
df_clean[df_clean['property_use_code']=='VRES1 - VACANT RESIDENTIAL 1']

roll_number  street_number unit_number street_direction  street_name  \
34    12080305500          534.0         NaN              NaN        CRAIG   
236   12080530000         1270.0         NaN              NaN     WOLSELEY   
701   12081184000         1064.0         NaN              NaN   PALMERSTON   
704   12081189100          104.0         NaN                S     GARFIELD   
919   12081435000         1020.0         NaN              NaN   PALMERSTON   
989   12081510000           35.0         NaN              NaN       AUBREY   
990   12081519200          139.0         NaN              NaN       AUBREY   
1222  12081806000           49.0         NaN              NaN       LENORE   
1223  12081807000           55.0         NaN              NaN       LENORE   
1596  12082275000          165.0         NaN              NaN      EVANSON   
1915  12082721100          850.0         NaN              NaN   PALMERSTON   
1968  12082784000          852.0         NaN              NaN  WESTMINSTER   
2462  12090208000           17.0         NaN              NaN      ALLOWAY   
2523  12097511500          547.0           1              NaN       NEWMAN   

     street_type            full_address neighbourhood_area  \
34        STREET        534 CRAIG STREET           WOLSELEY   
236       AVENUE    1270 WOLSELEY AVENUE           WOLSELEY   
701       AVENUE  1064 PALMERSTON AVENUE           WOLSELEY   
704       STREET   104 GARFIELD STREET S           WOLSELEY   
919       AVENUE  1020 PALMERSTON AVENUE           WOLSELEY   
989       STREET        35 AUBREY STREET           WOLSELEY   
990       STREET       139 AUBREY STREET           WOLSELEY   
1222      STREET        49 LENORE STREET           WOLSELEY   
1223      STREET        55 LENORE STREET           WOLSELEY   
1596      STREET      165 EVANSON STREET           WOLSELEY   
1915      AVENUE   850 PALMERSTON AVENUE           WOLSELEY   
1968      AVENUE  852 WESTMINSTER AVENUE           WOLSELEY   
2462      AVENUE       17 ALLOWAY AVENUE           WOLSELEY   
2523      STREET     1-547 NEWMAN STREET           WOLSELEY   

                 property_use_code  assessed_land_area                 zoning  \
34    VRES1 - VACANT RESIDENTIAL 1              3475.0  R2 - RES - TWO FAMILY   
236   VRES1 - VACANT RESIDENTIAL 1             18092.0  R2 - RES - TWO FAMILY   
701   VRES1 - VACANT RESIDENTIAL 1              5250.0  R2 - RES - TWO FAMILY   
704   VRES1 - VACANT RESIDENTIAL 1              7125.0  R2 - RES - TWO FAMILY   
919   VRES1 - VACANT RESIDENTIAL 1              4255.0  R2 - RES - TWO FAMILY   
989   VRES1 - VACANT RESIDENTIAL 1             25799.0  R2 - RES - TWO FAMILY   
990   VRES1 - VACANT RESIDENTIAL 1             16324.0  R2 - RES - TWO FAMILY   
1222  VRES1 - VACANT RESIDENTIAL 1              3051.0  R2 - RES - TWO FAMILY   
1223  VRES1 - VACANT RESIDENTIAL 1              6101.0  R2 - RES - TWO FAMILY   
1596  VRES1 - VACANT RESIDENTIAL 1              2444.0  R2 - RES - TWO FAMILY   
1915  VRES1 - VACANT RESIDENTIAL 1              5400.0  R2 - RES - TWO FAMILY   
1968  VRES1 - VACANT RESIDENTIAL 1              4405.0  R2 - RES - TWO FAMILY   
2462  VRES1 - VACANT RESIDENTIAL 1              3053.0  R2 - RES - TWO FAMILY   
2523  VRES1 - VACANT RESIDENTIAL 1              3710.0  R2 - RES - TWO FAMILY   

      total_assessed_value         assessment_date  \
34                214000.0  04/01/2023 12:00:00 AM   
236               522000.0  04/01/2023 12:00:00 AM   
701               442000.0  04/01/2023 12:00:00 AM   
704               438000.0  04/01/2023 12:00:00 AM   
919               430000.0  04/01/2023 12:00:00 AM   
989               400000.0  04/01/2023 12:00:00 AM   
990               369000.0  04/01/2023 12:00:00 AM   
1222              222000.0  04/01/2023 12:00:00 AM   
1223              250000.0  04/01/2023 12:00:00 AM   
1596              231000.0  04/01/2023 12:00:00 AM   
1915              443000.0  04/01/2023 12:00:00 AM   
1968              223000.

In [57]:
# Which it is! Drop vacants in new clean data frame 'wolseley'
wolseley = df_clean.drop(vacants_index, axis=0)

In [58]:
# And trim off excess columns
wolseley = wolseley[['roll_number', 'street_number', 'unit_number','street_name', 'street_type', 'full_address','property_use_code', 'assessed_land_area', 'zoning', 'total_assessed_value','property_class_1', 'geometry', 'centroid_lat', 'centroid_lon']]

In [59]:
wolseley

roll_number  street_number unit_number street_name street_type  \
3     12080260000          542.0         NaN      RAGLAN        ROAD   
4     12080261000          538.0         NaN      RAGLAN        ROAD   
5     12080262000          528.0         NaN      RAGLAN        ROAD   
6     12080263000          522.0         NaN      RAGLAN        ROAD   
9     12080265000         1338.0         NaN    WOLSELEY      AVENUE   
...           ...            ...         ...         ...         ...   
2666  12097805100           54.0         401    MARYLAND      STREET   
2667  12097805105           54.0         402    MARYLAND      STREET   
2668  12097806720          205.0         NaN   ARLINGTON      STREET   
2669  12097809455          510.0         NaN      NEWMAN      STREET   
2670  12097809460          518.0         NaN      NEWMAN      STREET   

                full_address                 property_use_code  \
3            542 RAGLAN ROAD  RESSD - DETACHED SINGLE DWELLING   
4            538 RAGLAN ROAD  RESSD - DETACHED SINGLE DWELLING   
5            528 RAGLAN ROAD  RESSD - DETACHED SINGLE DWELLING   
6            522 RAGLAN ROAD  RESSD - DETACHED SINGLE DWELLING   
9       1338 WOLSELEY AVENUE  RESSD - DETACHED SINGLE DWELLING   
...                      ...                               ...   
2666  401-54 MARYLAND STREET           CNAPT - CONDO APARTMENT   
2667  402-54 MARYLAND STREET           CNAPT - CONDO APARTMENT   
2668    205 ARLINGTON STREET                RESAP - APARTMENTS   
2669       510 NEWMAN STREET  RESSD - DETACHED SINGLE DWELLING   
2670       518 NEWMAN STREET  RESSD - DETACHED SINGLE DWELLING   

      assessed_land_area                 zoning  total_assessed_value  \
3                 5997.0  R2 - RES - TWO FAMILY              305000.0   
4                 5997.0  R2 - RES - TWO FAMILY              364000.0   
5                 5997.0  R2 - RES - TWO FAMILY              386000.0   
6                 5997.0  R2 - RES - TWO FAMILY              376000.0   
9                18720.0  R2 - RES - TWO FAMILY             1385000.0   
...                  ...                    ...                   ...   
2666                 NaN                    NaN              237000.0   
2667                 NaN                    NaN              225000.0   
2668             10643.0  R2 - RES - TWO FAMILY             1445000.0   
2669              2863.0  R2 - RES - TWO FAMILY              469000.0   
2670              5022.0  R2 - RES - TWO FAMILY              466000.0   

     property_class_1                                           geometry  \
3       RESIDENTIAL 1  MULTIPOLYGON (((-97.19102616382078 49.88138204...   
4       RESIDENTIAL 1  MULTIPOLYGON (((-97.19102616382078 49.88138204...   
5       RESIDENTIAL 1  MULTIPOLYGON (((-97.19104728492096 49.88110837...   
6       RESIDENTIAL 1  MULTIPOLYGON (((-97.19105784468728 49.88097154...   
9       RESIDENTIAL 1  MULTIPOLYGON (((-97.19051852774297 49.87921209...   
...               ...                                                ...   
2666    RESIDENTIAL 3  MULTIPOLYGON (((-97.16161542279819 49.88054499...   
2667    RESIDENTIAL 3  MULTIPOLYGON (((-97.16161542279819 49.88054499...   
2668    RESIDENTIAL 2  MULTIPOLYGON (((-97.16939763322243 49.88371190...   
2669    RESIDENTIAL 1  MULTIPOLYGON (((-97.18414267002349 49.88215925...   
2670    RESIDENTIAL 1  MULTIPOLYGON (((-97.18413124211199 49.88230564...   

      centroid_lat  centroid_lon  
3        49.881459    -97.191275  
4        49.881322    -97.191286  
5        49.881185    -97.191296  
6        49.881048    -97.191307  
9        49.878845    -97.190766  
...            ...           ...  
2666     49.880481    -97.161407  
2667     49.880481    -97.161407  
2668     49.883560    -97.169196  
2669     49.882111    -97.183947  
2670     49.882226    -97.183938  

[2624 rows x 14 columns]

In [60]:
wolseley.to_csv("wolseley_all.csv", encoding = "utf8")

## CONDO AND APARTMENTS

Here's the situation: 

Some of these addresses are condo buildings or apartment buildings, while others are individual units. 

I ultimately want to analyze both average property values and concentration of gardens on each street relative to the number of dwelligs. 

Which means I need to sort out the most accurate way to deal with these multi-unit buildings.

In [61]:
# Let's see what we're working with first

wolseley.property_use_code.value_counts()

property_use_code
RESSD - DETACHED SINGLE DWELLING          1942
RESMC - MULTIFAMILY CONVERSION             351
CNAPT - CONDO APARTMENT                    118
RESDU - DUPLEX                              45
RESAP - APARTMENTS                          35
CMRST - STORE                               28
CNRES - CONDO RESIDENTIAL                   26
CMOFF - OFFICE                              16
CNCMP - CONDO COMPLEX                        9
RESSS - SIDE BY SIDE                         8
RESSU - RESIDENTIAL SECONDARY UNIT           4
RESMA - MULTIPLE ATTACHED UNITS              4
RESTR - TRIPLEX                              4
RESGC - RESIDENTIAL GROUP CARE               4
CMCMU - COMMERCIAL MULTIPLE USE              3
RESMU - RESIDENTIAL MULTIPLE USE             3
VRES1 - VACANT RESIDENTIAL 1                 3
CMSTP - STRIP MALL                           3
CMRRE - RESTAURANT                           3
RESAM - APARTMENTS MULTIPLE USE              2
CMMRH - COMMERCIAL ROW HOUSE              

In [62]:
# Does everything listed as a 'Condo Apartment' have a unit number?

wolseley[wolseley['property_use_code'] == 'CNAPT - CONDO APARTMENT'].unit_number.isna().value_counts()

unit_number
False    118
Name: count, dtype: int64

In [63]:
# What are the 'Condo Complex' and 'Condo Residential' categories? 

wolseley[wolseley['property_use_code'] == 'CNCMP - CONDO COMPLEX']

roll_number  street_number unit_number street_name street_type  \
1227  12081813100           81.0         NaN      LENORE      STREET   
2319  12090045000           70.0         NaN    MARYLAND      STREET   
2527  12097530900          272.0         NaN        HOME      STREET   
2530  12097627600          828.0         NaN     PRESTON      AVENUE   
2567  12097644000          246.0         NaN        HOME      STREET   
2608  12097696700           52.0         NaN     FAWCETT      AVENUE   
2623  12097705900          504.0         NaN    DOMINION      STREET   
2632  12097775000           28.0         NaN     WOODROW       PLACE   
2658  12097805060           54.0         NaN    MARYLAND      STREET   

             full_address      property_use_code  assessed_land_area  \
1227     81 LENORE STREET  CNCMP - CONDO COMPLEX                 NaN   
2319   70 MARYLAND STREET  CNCMP - CONDO COMPLEX                 NaN   
2527      272 HOME STREET  CNCMP - CONDO COMPLEX                 NaN   
2530   828 PRESTON AVENUE  CNCMP - CONDO COMPLEX                 NaN   
2567      246 HOME STREET  CNCMP - CONDO COMPLEX                 NaN   
2608    52 FAWCETT AVENUE  CNCMP - CONDO COMPLEX                 NaN   
2623  504 DOMINION STREET  CNCMP - CONDO COMPLEX                 NaN   
2632     28 WOODROW PLACE  CNCMP - CONDO COMPLEX                 NaN   
2658   54 MARYLAND STREET  CNCMP - CONDO COMPLEX                 NaN   

                         zoning  total_assessed_value property_class_1  \
1227      R2 - RES - TWO FAMILY                   NaN              NaN   
2319  RMFM - RES - MULTI-FAMILY                   NaN              NaN   
2527      R2 - RES - TWO FAMILY                   NaN              NaN   
2530                        NaN                   NaN              NaN   
2567      R2 - RES - TWO FAMILY                   NaN              NaN   
2608                        NaN                   NaN              NaN   
2623                        NaN                   NaN              NaN   
2632      R2 - RES - TWO FAMILY                   NaN              NaN   
2658  RMFM - RES - MULTI-FAMILY                   NaN              NaN   

                                               geometry  centroid_lat  \
1227  MULTIPOLYGON (((-97.17170754959602 49.88003182...     49.879933   
2319  MULTIPOLYGON (((-97.1615777722684 49.881076916...     49.880870   
2527  MULTIPOLYGON (((-97.16879391698427 49.88495781...     49.884951   
2530  MULTIPOLYGON (((-97.16815998526683 49.88397379...     49.883809   
2567  MULTIPOLYGON (((-97.16885735853232 49.88410122...     49.884208   
2608  MULTIPOLYGON (((-97.16318119679728 49.88423481...     49.884095   
2623  MULTIPOLYGON (((-97.17899854702819 49.88181744...     49.881743   
2632  MULTIPOLYGON (((-97.16196857341524 49.87948783...     49.879221   
2658  MULTIPOLYGON (((-97.16161542279819 49.88054499...     49.880481   

      centroid_lon  
1227    -97.171493  
2319    -97.161386  
2527    -97.168581  
2530    -97.167931  
2567    -97.168636  
2608    -97.163083  
2623    -97.178793  
2632    -97.161889  
2658    -97.161407

In [64]:
wolseley[wolseley['property_use_code'] == 'CNRES - CONDO RESIDENTIAL']

roll_number  street_number unit_number street_name street_type  \
1228  12081813200           81.0           1      LENORE      STREET   
1229  12081813300           83.0           3      LENORE      STREET   
1230  12081813400           81.0           2      LENORE      STREET   
1231  12081813500           83.0           4      LENORE      STREET   
2320  12090045100           70.0         101    MARYLAND      STREET   
2321  12090045200           70.0         102    MARYLAND      STREET   
2322  12090045300           70.0         103    MARYLAND      STREET   
2323  12090045400           70.0         104    MARYLAND      STREET   
2324  12090045500           70.0         105    MARYLAND      STREET   
2325  12090045600           70.0         106    MARYLAND      STREET   
2326  12090045700           70.0         107    MARYLAND      STREET   
2327  12090045800           70.0         108    MARYLAND      STREET   
2328  12090045900           70.0         109    MARYLAND      STREET   
2329  12090046000           70.0         110    MARYLAND      STREET   
2330  12090046100           70.0         111    MARYLAND      STREET   
2331  12090046200           70.0         112    MARYLAND      STREET   
2332  12090046300           70.0         113    MARYLAND      STREET   
2333  12090046400           70.0         114    MARYLAND      STREET   
2334  12090046500           70.0         115    MARYLAND      STREET   
2335  12090046600           70.0         116    MARYLAND      STREET   
2336  12090046700           70.0         117    MARYLAND      STREET   
2337  12090046800           70.0         118    MARYLAND      STREET   
2338  12090046900           70.0         119    MARYLAND      STREET   
2339  12090047000           70.0         120    MARYLAND      STREET   
2630  12097751400            3.0         NaN     PURCELL      AVENUE   
2631  12097751500            5.0         NaN     PURCELL      AVENUE   

                full_address          property_use_code  assessed_land_area  \
1228      1-81 LENORE STREET  CNRES - CONDO RESIDENTIAL                 NaN   
1229      3-83 LENORE STREET  CNRES - CONDO RESIDENTIAL                 NaN   
1230      2-81 LENORE STREET  CNRES - CONDO RESIDENTIAL                 NaN   
1231      4-83 LENORE STREET  CNRES - CONDO RESIDENTIAL                 NaN   
2320  101-70 MARYLAND STREET  CNRES - CONDO RESIDENTIAL                 NaN   
2321  102-70 MARYLAND STREET  CNRES - CONDO RESIDENTIAL                 NaN   
2322  103-70 MARYLAND STREET  CNRES - CONDO RESIDENTIAL                 NaN   
2323  104-70 MARYLAND STREET  CNRES - CONDO RESIDENTIAL                 NaN   
2324  105-70 MARYLAND STREET  CNRES - CONDO RESIDENTIAL                 NaN   
2325  106-70 MARYLAND STREET  CNRES - CONDO RESIDENTIAL                 NaN   
2326  107-70 MARYLAND STREET  CNRES - CONDO RESIDENTIAL                 NaN   
2327  108-70 MARYLAND STREET  CNRES - CONDO RESIDENTIAL                 NaN   
2328  109-70 MARYLAND STREET  CNRES - CONDO RESIDENTIAL                 NaN   
2329  110-70 MARYLAND STREET  CNRES - CONDO RESIDENTIAL                 NaN   
2330  111-70 MARYLAND STREET  CNRES - CONDO RESIDENTIAL                 NaN   
2331  112-70 MARYLAND STREET  CNRES - CONDO RESIDENTIAL                 NaN   
2332  113-70 MARYLAND STREET  CNRES - CONDO RESIDENTIAL                 NaN   
2333  114-70 MARYLAND STREET  CNRES - CONDO RESIDENTIAL                 NaN   
2334  115-70 MARYLAND STREET  CNRES - CONDO RESIDENTIAL                 NaN   
2335  116-70 MARYLAND STREET  CNRES - CONDO RESIDENTIAL                 NaN   
2336  117-70 MARYLAND STREET  CNRES - CONDO RESIDENTIAL                 NaN   
2337  118-70 MARYLAND STREET  CNRES - CONDO RESIDENTIAL                 NaN   
2338  119-70 MARYLAND STREET  CNRES - CONDO RESIDENTIAL                 NaN   
2339  120-70 MARYLAND STREET  CNRES - CONDO RESIDENTIAL                 NaN   
2630        3 PURCELL AVENUE  CNRES - CONDO RESIDENTIAL                 NaN   
2631   

Here's what we've got:

Condo complex refers to the larger condo building itself. It has no property value, and represents any number of units 
Condo residential and condo apartments refers to individual units, which do have values, but would count as multiple dwellings on a street, for example.

The way I am collecting garden data is by address number. There are a few cases where this _does_ refer to a multi-unit building. For example, across the street from me is a seniors facility where the ladies love gardening, and have planted on the boulevard  on all three sides of the building. There are SEVERAL units, and I can't guess who is responsible for each garden (I mean, in some cases I know, but it's because they are my neighbours), so the gardens are all attributed to the one building. 

In this situation, I want to have one row for that condo building that I can attribute the garden to, but still average the property values of all the units. I also need to decide whether I am counting the number of _buildings_ on a street for the relative garden concentration, or the number of _dwellings_ (which I would define as each individual unit). 

So I need to make an editorial decision.

At this point in time, my idea is this:

Wolseley is a mixed density neighbourhood. There are commercial properties in residential buildings, condos, apartments, duplexes, triplexes, multi-use houses, etc. It would be futile to try and untangle ALL of these use classes and try to attribute a garden to one individual in an apartment, a condo, an assisted living facility, etc. The most important data in this story is the number of gardens on the block. Therefore, I am going to treat each BUILDING as a distinct object, regardless of how many different units it contains. It is, after all, the building — **the LOT** — which has access to a boulevard. 

This means the aggregation I need to do is assigning an average property value to a multi-unit building so that data is still captured. 

From what I can see in the geojson of this data, the issue is specific to condos, because condo units are owned and sold individually and therefore can have individual property values, whereas an apartment building has a value for the whole plot the building itself is on (note to self that this will skew the property values on blocks with apartments, but that's a problem for later). That means I only need to do this aggregation for condos.

In [65]:
# Steps:
# Find all the condo complexes and the associated apartments
# For each of the complexes, find the mean property value for associated apartments
# Save that average value to the property value column for the complex
# Drop apartment rows

In [66]:
wolseley[wolseley['property_use_code'].isin(['CNRES - CONDO RESIDENTIAL','CNAPT - CONDO APARTMENT','CNCMP - CONDO COMPLEX'])]

roll_number  street_number unit_number street_name street_type  \
1227  12081813100           81.0         NaN      LENORE      STREET   
1228  12081813200           81.0           1      LENORE      STREET   
1229  12081813300           83.0           3      LENORE      STREET   
1230  12081813400           81.0           2      LENORE      STREET   
1231  12081813500           83.0           4      LENORE      STREET   
...           ...            ...         ...         ...         ...   
2663  12097805085           54.0         301    MARYLAND      STREET   
2664  12097805090           54.0         302    MARYLAND      STREET   
2665  12097805095           54.0         303    MARYLAND      STREET   
2666  12097805100           54.0         401    MARYLAND      STREET   
2667  12097805105           54.0         402    MARYLAND      STREET   

                full_address          property_use_code  assessed_land_area  \
1227        81 LENORE STREET      CNCMP - CONDO COMPLEX                 NaN   
1228      1-81 LENORE STREET  CNRES - CONDO RESIDENTIAL                 NaN   
1229      3-83 LENORE STREET  CNRES - CONDO RESIDENTIAL                 NaN   
1230      2-81 LENORE STREET  CNRES - CONDO RESIDENTIAL                 NaN   
1231      4-83 LENORE STREET  CNRES - CONDO RESIDENTIAL                 NaN   
...                      ...                        ...                 ...   
2663  301-54 MARYLAND STREET    CNAPT - CONDO APARTMENT                 NaN   
2664  302-54 MARYLAND STREET    CNAPT - CONDO APARTMENT                 NaN   
2665  303-54 MARYLAND STREET    CNAPT - CONDO APARTMENT                 NaN   
2666  401-54 MARYLAND STREET    CNAPT - CONDO APARTMENT                 NaN   
2667  402-54 MARYLAND STREET    CNAPT - CONDO APARTMENT                 NaN   

                     zoning  total_assessed_value property_class_1  \
1227  R2 - RES - TWO FAMILY                   NaN              NaN   
1228                    NaN              265000.0    RESIDENTIAL 2   
1229                    NaN              282000.0    RESIDENTIAL 2   
1230                    NaN              291000.0    RESIDENTIAL 3   
1231                    NaN              287000.0    RESIDENTIAL 3   
...                     ...                   ...              ...   
2663                    NaN              222000.0    RESIDENTIAL 3   
2664                    NaN              167000.0    RESIDENTIAL 2   
2665                    NaN              192000.0    RESIDENTIAL 3   
2666                    NaN              237000.0    RESIDENTIAL 3   
2667                    NaN              225000.0    RESIDENTIAL 3   

                                               geometry  centroid_lat  \
1227  MULTIPOLYGON (((-97.17170754959602 49.88003182...     49.879933   
1228  MULTIPOLYGON (((-97.17170754959602 49.88003182...     49.879933   
1229  MULTIPOLYGON (((-97.17170754959602 49.88003182...     49.879933   
1230  MULTIPOLYGON (((-97.17170754959602 49.88003182...     49.879933   
1231  MULTIPOLYGON (((-97.17170754959602 49.88003182...     49.879933   
...                                                 ...           ...   
2663  MULTIPOLYGON (((-97.16161542279819 49.88054499...     49.880481   
2664  MULTIPOLYGON (((-97.16161542279819 49.88054499...     49.880481   
2665  MULTIPOLYGON (((-97.16161542279819 49.88054499...     49.880481   
2666  MULTIPOLYGON (((-97.16161542279819 49.88054499...     49.880481   
2667  MULTIPOLYGON (((-97.16161542279819 49.88054499...     49.880481   

      centroid_lon  
1227    -97.171493  
1228    -97.171493  
1229    -97.171493  
1230    -97.171493  
1231    -97.171493  
...            ...  
2663    -97.161407  
2664    -97.161407  
2665    -97.161407  
2666    -97.161407  
2667    -97.161407  

[153 rows x 14 columns]

In [67]:
condos = wolseley[wolseley['property_use_code'].isin(['CNRES - CONDO RESIDENTIAL','CNAPT - CONDO APARTMENT','CNCMP - CONDO COMPLEX'])]

In [68]:
condos.groupby(['street_name', 'street_number']).total_assessed_value.mean()

street_name  street_number
DOMINION     504.0            214500.000000
             506.0            219000.000000
FAWCETT      52.0             124071.428571
HOME         246.0            107428.571429
             272.0            182466.666667
LENORE       81.0             278000.000000
             83.0             284500.000000
MARYLAND     54.0             205125.000000
             70.0             196000.000000
PRESTON      828.0            142527.777778
PURCELL      3.0              238000.000000
             5.0              238000.000000
WOODROW      28.0              65350.000000
Name: total_assessed_value, dtype: float64

In [69]:
condos[condos['unit_number'].isna()]

roll_number  street_number unit_number street_name street_type  \
1227  12081813100           81.0         NaN      LENORE      STREET   
2319  12090045000           70.0         NaN    MARYLAND      STREET   
2527  12097530900          272.0         NaN        HOME      STREET   
2530  12097627600          828.0         NaN     PRESTON      AVENUE   
2567  12097644000          246.0         NaN        HOME      STREET   
2608  12097696700           52.0         NaN     FAWCETT      AVENUE   
2623  12097705900          504.0         NaN    DOMINION      STREET   
2630  12097751400            3.0         NaN     PURCELL      AVENUE   
2631  12097751500            5.0         NaN     PURCELL      AVENUE   
2632  12097775000           28.0         NaN     WOODROW       PLACE   
2658  12097805060           54.0         NaN    MARYLAND      STREET   

             full_address          property_use_code  assessed_land_area  \
1227     81 LENORE STREET      CNCMP - CONDO COMPLEX                 NaN   
2319   70 MARYLAND STREET      CNCMP - CONDO COMPLEX                 NaN   
2527      272 HOME STREET      CNCMP - CONDO COMPLEX                 NaN   
2530   828 PRESTON AVENUE      CNCMP - CONDO COMPLEX                 NaN   
2567      246 HOME STREET      CNCMP - CONDO COMPLEX                 NaN   
2608    52 FAWCETT AVENUE      CNCMP - CONDO COMPLEX                 NaN   
2623  504 DOMINION STREET      CNCMP - CONDO COMPLEX                 NaN   
2630     3 PURCELL AVENUE  CNRES - CONDO RESIDENTIAL                 NaN   
2631     5 PURCELL AVENUE  CNRES - CONDO RESIDENTIAL                 NaN   
2632     28 WOODROW PLACE      CNCMP - CONDO COMPLEX                 NaN   
2658   54 MARYLAND STREET      CNCMP - CONDO COMPLEX                 NaN   

                         zoning  total_assessed_value property_class_1  \
1227      R2 - RES - TWO FAMILY                   NaN              NaN   
2319  RMFM - RES - MULTI-FAMILY                   NaN              NaN   
2527      R2 - RES - TWO FAMILY                   NaN              NaN   
2530                        NaN                   NaN              NaN   
2567      R2 - RES - TWO FAMILY                   NaN              NaN   
2608                        NaN                   NaN              NaN   
2623                        NaN                   NaN              NaN   
2630                        NaN              238000.0    RESIDENTIAL 2   
2631                        NaN              238000.0    RESIDENTIAL 2   
2632      R2 - RES - TWO FAMILY                   NaN              NaN   
2658  RMFM - RES - MULTI-FAMILY                   NaN              NaN   

                                               geometry  centroid_lat  \
1227  MULTIPOLYGON (((-97.17170754959602 49.88003182...     49.879933   
2319  MULTIPOLYGON (((-97.1615777722684 49.881076916...     49.880870   
2527  MULTIPOLYGON (((-97.16879391698427 49.88495781...     49.884951   
2530  MULTIPOLYGON (((-97.16815998526683 49.88397379...     49.883809   
2567  MULTIPOLYGON (((-97.16885735853232 49.88410122...     49.884208   
2608  MULTIPOLYGON (((-97.16318119679728 49.88423481...     49.884095   
2623  MULTIPOLYGON (((-97.17899854702819 49.88181744...     49.881743   
2630  MULTIPOLYGON (((-97.16144826624206 49.88290017...     49.882840   
2631  MULTIPOLYGON (((-97.16144826624206 49.88290017...     49.882840   
2632  MULTIPOLYGON (((-97.16196857341524 49.87948783...     49.879221   
2658  MULTIPOLYGON (((-97.16161542279819 49.88054499...     49.880481   

      centroid_lon  
1227    -97.171493  
2319    -97.161386  
2527    -97.168581  
2530    -97.167931  
2567    -97.168636  
2608    -97.163083  
2623    -97.178793  
2630    -97.161247  
2631    -97.161247  
2632    -97.161889  
2658    -97.161407

In [70]:
condos.groupby(['street_name']).total_assessed_value.mean()

street_name
DOMINION    216750.000000
FAWCETT     124071.428571
HOME        138694.444444
LENORE      281250.000000
MARYLAND    198607.142857
PRESTON     142527.777778
PURCELL     238000.000000
WOODROW      65350.000000
Name: total_assessed_value, dtype: float64

In [71]:
# Couple scenarios at play here: 
# The condos on Dominion and Lenore are one complex but the units have two street addresses.
# Whereas Home and Maryland have two separate complexes
# I feel the best approach here will be manual because I have no clue what else to do!

In [72]:
# street_name  number         total_assessed_value    index
# WOODROW      28.0              65350.000000          2632
# PRESTON      828.0            142527.777778          2530
# FAWCETT      52.0             124071.428571          2608
# HOME         246.0            107428.571429          2567
# HOME         272.0            182466.666667          2527
# MARYLAND     54.0             205125.000000          2658
# MARYLAND     70.0             196000.000000          2319
# DOMINION     504.0            216750.000000          2623
# LENORE       81.0             281250.000000          1227

In [73]:
wolseley.loc[2632, 'total_assessed_value'] = 65350.000000
wolseley.loc[2530, 'total_assessed_value'] = 142527.777778
wolseley.loc[2608, 'total_assessed_value'] = 124071.428571
wolseley.loc[2567, 'total_assessed_value'] = 107428.571429
wolseley.loc[2527, 'total_assessed_value'] = 182466.666667
wolseley.loc[2658, 'total_assessed_value'] = 205125.000000
wolseley.loc[2319, 'total_assessed_value'] = 196000.000000
wolseley.loc[2623, 'total_assessed_value'] = 216750.000000 
wolseley.loc[1227, 'total_assessed_value'] = 281250.000000

In [74]:
wolseley[wolseley['property_use_code']=='CNCMP - CONDO COMPLEX']

roll_number  street_number unit_number street_name street_type  \
1227  12081813100           81.0         NaN      LENORE      STREET   
2319  12090045000           70.0         NaN    MARYLAND      STREET   
2527  12097530900          272.0         NaN        HOME      STREET   
2530  12097627600          828.0         NaN     PRESTON      AVENUE   
2567  12097644000          246.0         NaN        HOME      STREET   
2608  12097696700           52.0         NaN     FAWCETT      AVENUE   
2623  12097705900          504.0         NaN    DOMINION      STREET   
2632  12097775000           28.0         NaN     WOODROW       PLACE   
2658  12097805060           54.0         NaN    MARYLAND      STREET   

             full_address      property_use_code  assessed_land_area  \
1227     81 LENORE STREET  CNCMP - CONDO COMPLEX                 NaN   
2319   70 MARYLAND STREET  CNCMP - CONDO COMPLEX                 NaN   
2527      272 HOME STREET  CNCMP - CONDO COMPLEX                 NaN   
2530   828 PRESTON AVENUE  CNCMP - CONDO COMPLEX                 NaN   
2567      246 HOME STREET  CNCMP - CONDO COMPLEX                 NaN   
2608    52 FAWCETT AVENUE  CNCMP - CONDO COMPLEX                 NaN   
2623  504 DOMINION STREET  CNCMP - CONDO COMPLEX                 NaN   
2632     28 WOODROW PLACE  CNCMP - CONDO COMPLEX                 NaN   
2658   54 MARYLAND STREET  CNCMP - CONDO COMPLEX                 NaN   

                         zoning  total_assessed_value property_class_1  \
1227      R2 - RES - TWO FAMILY         281250.000000              NaN   
2319  RMFM - RES - MULTI-FAMILY         196000.000000              NaN   
2527      R2 - RES - TWO FAMILY         182466.666667              NaN   
2530                        NaN         142527.777778              NaN   
2567      R2 - RES - TWO FAMILY         107428.571429              NaN   
2608                        NaN         124071.428571              NaN   
2623                        NaN         216750.000000              NaN   
2632      R2 - RES - TWO FAMILY          65350.000000              NaN   
2658  RMFM - RES - MULTI-FAMILY         205125.000000              NaN   

                                               geometry  centroid_lat  \
1227  MULTIPOLYGON (((-97.17170754959602 49.88003182...     49.879933   
2319  MULTIPOLYGON (((-97.1615777722684 49.881076916...     49.880870   
2527  MULTIPOLYGON (((-97.16879391698427 49.88495781...     49.884951   
2530  MULTIPOLYGON (((-97.16815998526683 49.88397379...     49.883809   
2567  MULTIPOLYGON (((-97.16885735853232 49.88410122...     49.884208   
2608  MULTIPOLYGON (((-97.16318119679728 49.88423481...     49.884095   
2623  MULTIPOLYGON (((-97.17899854702819 49.88181744...     49.881743   
2632  MULTIPOLYGON (((-97.16196857341524 49.87948783...     49.879221   
2658  MULTIPOLYGON (((-97.16161542279819 49.88054499...     49.880481   

      centroid_lon  
1227    -97.171493  
2319    -97.161386  
2527    -97.168581  
2530    -97.167931  
2567    -97.168636  
2608    -97.163083  
2623    -97.178793  
2632    -97.161889  
2658    -97.161407

In [75]:
# Now to drop the condo apartments

condo_apartments = wolseley[wolseley['property_use_code']== 'CNAPT - CONDO APARTMENT'].index
wolseley= wolseley.drop(condo_apartments,axis=0)

In [76]:
condo_apartments_2 = wolseley[(wolseley['property_use_code']== 'CNRES - CONDO RESIDENTIAL') & (wolseley['street_name']!= 'PURCELL')].index
wolseley= wolseley.drop(condo_apartments_2,axis=0)

In [77]:
wolseley.info()

<class 'pandas.core.frame.DataFrame'>
Index: 2482 entries, 3 to 2670
Data columns (total 14 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   roll_number           2482 non-null   int64  
 1   street_number         2482 non-null   float64
 2   unit_number           6 non-null      object 
 3   street_name           2482 non-null   object 
 4   street_type           2473 non-null   object 
 5   full_address          2482 non-null   object 
 6   property_use_code     2482 non-null   object 
 7   assessed_land_area    2470 non-null   float64
 8   zoning                2476 non-null   object 
 9   total_assessed_value  2482 non-null   float64
 10  property_class_1      2473 non-null   object 
 11  geometry              2482 non-null   object 
 12  centroid_lat          2482 non-null   float64
 13  centroid_lon          2482 non-null   float64
dtypes: float64(5), int64(1), object(8)
memory usage: 290.9+ KB


In [78]:
# I think this is close enough. At least for a first project.

## Merging garden data:

The time has come to read in the data that really matters - the garden data!

### **Garden methodology:**

Over the course of three days, I walked or cycled the length of every street in the Wolseley neighbourhood, using a paper street map as a guide, and recorded the street number and street name of each boulevard garden I saw. 

There are some important methodology notes to keep in mind:

- A boulevard garden is defined as a planted garden on the city-owned portion of the roadway. In most cases, this is the strip of vegetation between the road and the sidewalk. In the case of a street with no sidewalk, this is defined as vegetation that reaches all the way to the curb with no visible grass between the property line and the roadway.
- A boulevard garden is defined as vegetation and other decoration where more than one type of vegetation has been intentionally planted. This is to exclude, most notably, patches of tiger lilies around the base of a tree, which are prolific in the neighbourhood, but may or may not have been planted by the resident. This is, of course, a subjective assessment. There is a chance some gardens were missed.
- Corner properties with gardens on both sides of the street have been recorded as one garden, but the location of the garden(s) is included in the notes.

This data includes a notes field. Throughout the collection process, if there were gardens that were uncertain, street numbers that were difficult to see or any other comment, it was recorded in the notes. Any questions about a particular point were later cross-referenced with satellite imagery, the latest available street view data or a second check when necessary.



In [106]:
# Read in gardens
gardens = pd.read_csv("wolseley_has_garden.csv")

In [107]:
gardens

street_number  street_name street_type              full_address  \
0              38      ALLOWAY      AVENUE         38 ALLOWAY AVENUE   
1              51      ALLOWAY      AVENUE         51 ALLOWAY AVENUE   
2             200    ARLINGTON      STREET      200 ARLINGTON STREET   
3              14    ARLINGTON      STREET       14 ARLINGTON STREET   
4              16    ARLINGTON      STREET       16 ARLINGTON STREET   
5              21    ARLINGTON      STREET       21 ARLINGTON STREET   
6              25    ARLINGTON      STREET       25 ARLINGTON STREET   
7              29    ARLINGTON      STREET       29 ARLINGTON STREET   
8              31    ARLINGTON      STREET       31 ARLINGTON STREET   
9              34    ARLINGTON      STREET       34 ARLINGTON STREET   
10             71    ARLINGTON      STREET       71 ARLINGTON STREET   
11             72    ARLINGTON      STREET       72 ARLINGTON STREET   
12             73    ARLINGTON      STREET       73 ARLINGTON STREET   
13             75    ARLINGTON      STREET       75 ARLINGTON STREET   
14             85    ARLINGTON      STREET       85 ARLINGTON STREET   
15            314       AUBREY      STREET         314 AUBREY STREET   
16            307       AUBREY      STREET         307 AUBREY STREET   
17            279       AUBREY      STREET         279 AUBREY STREET   
18            274       AUBREY      STREET         274 AUBREY STREET   
19            233       AUBREY      STREET         233 AUBREY STREET   
20            226       AUBREY      STREET         226 AUBREY STREET   
21            213       AUBREY      STREET         213 AUBREY STREET   
22            198       AUBREY      STREET         198 AUBREY STREET   
23            187       AUBREY      STREET         187 AUBREY STREET   
24            190       AUBREY      STREET         190 AUBREY STREET   
25            153       AUBREY      STREET         153 AUBREY STREET   
26            144       AUBREY      STREET         144 AUBREY STREET   
27             28       AUBREY      STREET          28 AUBREY STREET   
28             26       AUBREY      STREET          26 AUBREY STREET   
29             24       AUBREY      STREET          24 AUBREY STREET   
30             22       AUBREY      STREET          22 AUBREY STREET   
31            526     BASSWOOD       PLACE        526 BASSWOOD PLACE   
32            517     BASSWOOD       PLACE        517 BASSWOOD PLACE   
33            515     BASSWOOD       PLACE        515 BASSWOOD PLACE   
34            516     BASSWOOD       PLACE        516 BASSWOOD PLACE   
35            509     BASSWOOD       PLACE        509 BASSWOOD PLACE   
36            501     BASSWOOD       PLACE        501 BASSWOOD PLACE   
37            491     BASSWOOD       PLACE        491 BASSWOOD PLACE   
38            517       CAMDEN       PLACE          517 CAMDEN PLACE   
39            509       CAMDEN       PLACE          509 CAMDEN PLACE   
40            507       CAMDEN       PLACE          507 CAMDEN PLACE   
41            491       CAMDEN       PLACE          491 CAMDEN PLACE   
42            185       CANORA      STREET         185 CANORA STREET   
43            192       CANORA      STREET         192 CANORA STREET   
44            183       CANORA      STREET         183 CANORA STREET   
45            184       CANORA      STREET         184 CANORA STREET   
46            181       CANORA      STREET         181 CANORA STREET   
47            167       CANORA      STREET         167 CANORA STREET   
48            170       CANORA      STREET         170 CANORA STREET   
49            143       CANORA      STREET         143 CANORA STREET   
50            135       CANORA      STREET         135 CANORA STREET   
51            130       CANORA      STREET         130 CANORA STREET   
52            129       CANORA      STREET         129 CANORA STREET   
53            124       CANORA      STREET         124 CANORA STREET   
54            122       CANORA      STREET  

In [108]:
# Need to make sure all the address columns are aligned for a merge
gardens.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 358 entries, 0 to 357
Data columns (total 6 columns):
 #   Column         Non-Null Count  Dtype 
---  ------         --------------  ----- 
 0   street_number  358 non-null    object
 1   street_name    358 non-null    object
 2   street_type    358 non-null    object
 3   full_address   358 non-null    object
 4   has_garden     358 non-null    bool  
 5   notes          42 non-null     object
dtypes: bool(1), object(5)
memory usage: 14.5+ KB


In [109]:
wolseley.info()

<class 'pandas.core.frame.DataFrame'>
Index: 2482 entries, 3 to 2670
Data columns (total 14 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   roll_number           2482 non-null   int64  
 1   street_number         2482 non-null   object 
 2   unit_number           6 non-null      object 
 3   street_name           2482 non-null   object 
 4   street_type           2473 non-null   object 
 5   full_address          2482 non-null   object 
 6   property_use_code     2482 non-null   object 
 7   assessed_land_area    2470 non-null   float64
 8   zoning                2476 non-null   object 
 9   total_assessed_value  2482 non-null   float64
 10  property_class_1      2473 non-null   object 
 11  geometry              2482 non-null   object 
 12  centroid_lat          2482 non-null   float64
 13  centroid_lon          2482 non-null   float64
dtypes: float64(4), int64(1), object(9)
memory usage: 290.9+ KB


In [110]:
# Wolseley street number should be converted to string
wolseley = wolseley.astype({'street_number': 'object'})

In [142]:
# I am hoping to merge this sheet with the wolseley sheet, with all rows included and using 'full_address' to match

wolseley_gardens = pd.merge(wolseley, gardens, on=['full_address'], how='outer')

In [143]:
wolseley_gardens.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2484 entries, 0 to 2483
Data columns (total 19 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   roll_number           2482 non-null   float64
 1   street_number_x       2482 non-null   object 
 2   unit_number           6 non-null      object 
 3   street_name_x         2482 non-null   object 
 4   street_type_x         2473 non-null   object 
 5   full_address          2484 non-null   object 
 6   property_use_code     2482 non-null   object 
 7   assessed_land_area    2470 non-null   float64
 8   zoning                2476 non-null   object 
 9   total_assessed_value  2482 non-null   float64
 10  property_class_1      2473 non-null   object 
 11  geometry              2482 non-null   object 
 12  centroid_lat          2482 non-null   float64
 13  centroid_lon          2482 non-null   float64
 14  street_number_y       358 non-null    object 
 15  street_name_y        

In [131]:
# We have a few extra rows (7 in total) and I want to see them!

# wolseley_gardens[wolseley_gardens.roll_number.isna()]

#### Notes on extra rows:

- There is no 146 Ethelbert in the roll data, it's actually 144 Ethelbert (a duplex).
- Same is true for 82 (actually 80, a duplex)
- Same for 169 Canora (actually 167 per the roll)
- 91 Walnut is a typo (it's 81, thought I had fixed that already...)
- 927 Wolseley is also a duplex (should be 925)


I am going to fix these in the original spreadsheet and try again!
The old grace rows can stay, as that's an effor to reflect this building has gardens on 3 sides

In [132]:
# YAY! It's finally merged!

### Cleaning merged data for analysis:

In [144]:
# All I really need is: 
# roll_number, street_number, street_name, full_address, has_garden, total_assessed_value, property_use_code, geometry, centroid_lat, centroid_lon

wolseley_gardens = wolseley_gardens[['roll_number','full_address', 'has_garden', 'total_assessed_value', 'street_number_x', 'street_name_x', 'property_use_code', 'geometry', 'centroid_lat', 'centroid_lon']]

In [145]:
wolseley_gardens

roll_number              full_address has_garden  total_assessed_value  \
0     1.208178e+10           1 LENORE STREET        NaN          2.320000e+05   
1     1.208269e+10    1-130 ETHELBERT STREET        NaN          4.520000e+05   
2     1.208232e+10      1-156 EVANSON STREET        NaN          6.430000e+05   
3     1.208258e+10         1-230 HOME STREET        NaN          5.040000e+05   
4     1.208234e+10      1-273 EVANSON STREET        NaN          4.860000e+05   
5     1.209751e+10       1-547 NEWMAN STREET        NaN          2.320000e+05   
6     1.208218e+10         10 EVANSON STREET        NaN          3.280000e+05   
7     1.209775e+10          10 PICARDY PLACE        NaN          7.410000e+05   
8     1.208202e+10            10 RUBY STREET        NaN          3.510000e+05   
9     1.208224e+10      100 ARLINGTON STREET        NaN          2.740000e+05   
10    1.208219e+10        100 EVANSON STREET        NaN          4.070000e+05   
11    1.208247e+10           100 HOME STREET       True          4.710000e+05   
12    1.208198e+10         100 LENORE STREET        NaN          3.130000e+05   
13    1.208162e+10         100 LIPTON STREET        NaN          3.800000e+05   
14    1.209008e+10       100 MARYLAND STREET        NaN          1.762000e+06   
15    1.208128e+10       100 SHERBURN STREET        NaN          3.070000e+05   
16    1.208296e+10         100 WALNUT STREET        NaN          3.850000e+05   
17    1.208159e+10    1002 PALMERSTON AVENUE        NaN          6.270000e+05   
18    1.208159e+10    1004 PALMERSTON AVENUE        NaN          5.900000e+05   
19    1.208159e+10    1006 PALMERSTON AVENUE        NaN          4.630000e+05   
20    1.208249e+10           101 HOME STREET        NaN          3.550000e+05   
21    1.208170e+10         101 LIPTON STREET        NaN          3.390000e+05   
22    1.208195e+10           101 RUBY STREET        NaN          3.210000e+05   
23    1.208131e+10       101 SHERBURN STREET        NaN          2.890000e+05   
24    1.209781e+10    101-54 MARYLAND STREET        NaN          2.830000e+05   
25    1.208151e+10    1010 PALMERSTON AVENUE        NaN          5.520000e+05   
26    1.208161e+10      1010 WOLSELEY AVENUE        NaN          2.942000e+06   
27    1.208224e+10      102 ARLINGTON STREET        NaN          2.150000e+05   
28    1.208292e+10       102 CHESTNUT STREET        NaN          4.060000e+05   
29    1.208247e+10           102 HOME STREET        NaN          3.330000e+05   
30    1.208198e+10         102 LENORE STREET        NaN          2.990000e+05   
31    1.208162e+10         102 LIPTON STREET        NaN          2.850000e+05   
32    1.208206e+10           102 RUBY STREET        NaN          4.200000e+05   
33    1.208128e+10       102 SHERBURN STREET        NaN          3.920000e+05   
34    1.208294e+10       103 CHESTNUT STREET        NaN          4.900000e+05   
35    1.208182e+10         103 LENORE STREET        NaN          3.170000e+05   
36    1.208170e+10         103 LIPTON STREET        NaN          4.480000e+05   
37    1.208195e+10           103 RUBY STREET        NaN          3.580000e+05   
38    1.208131e+10       103 SHERBURN STREET       True          2.920000e+05   
39    1.208143e+10    1030 PALMERSTON AVENUE        NaN          8.830000e+05   
40    1.208144e+10    1031 PALMERSTON AVENUE       True          3.840000e+05   
41    1.208139e+10       1032 PORTAGE AVENUE        NaN          4.190000e+05   
42    1.208143e+10    1034 PALMERSTON AVENUE        NaN          6.630000e+05   
43    1.208139e+10       1036 PORTAGE AVENUE        NaN          4.660000e+05   
44    1.208143e+10    1038 PALMERSTON AVENUE        NaN          4.750000e+05   
45    1.208139e+10       1038 PORTAGE AVENUE        NaN          1.001000e+06   
46    1.208224e+10      104 ARLINGTON STREET        NaN          3.950000e+05   
47    1.208292e+10       104 CHESTNUT STREET       True          3.580000e+05   
48    1.208219e+10        104 EVANSON 

In [163]:
# Lovely! Three more steps:
# First, set has_garden null values to false

wolseley_gardens.has_garden.fillna(value=False, inplace=True)

In [159]:
# Next, fix the annoying format for both property values and roll numbers

# I found this on the internet (shrug)

pd.set_option('display.float_format', '{:.0f}'.format)

# To turn it off use: pd.reset_option('display.float_format')

In [169]:
# Finally, rename the street name and number columns

wolseley_gardens.rename(columns={'street_name_x':'street_name','street_number_x':'street_number'}, inplace=True)

In [170]:
wolseley_gardens

roll_number              full_address  has_garden  total_assessed_value  \
0     12081776000           1 LENORE STREET       False                232000   
1     12082691000    1-130 ETHELBERT STREET       False                452000   
2     12082318000      1-156 EVANSON STREET       False                643000   
3     12082580000         1-230 HOME STREET       False                504000   
4     12082345000      1-273 EVANSON STREET       False                486000   
5     12097511500       1-547 NEWMAN STREET       False                232000   
6     12082176000         10 EVANSON STREET       False                328000   
7     12097750000          10 PICARDY PLACE       False                741000   
8     12082022000            10 RUBY STREET       False                351000   
9     12082235000      100 ARLINGTON STREET       False                274000   
10    12082191000        100 EVANSON STREET       False                407000   
11    12082466000           100 HOME STREET        True                471000   
12    12081982000         100 LENORE STREET       False                313000   
13    12081624000         100 LIPTON STREET       False                380000   
14    12090076000       100 MARYLAND STREET       False               1762000   
15    12081275000       100 SHERBURN STREET       False                307000   
16    12082960000         100 WALNUT STREET       False                385000   
17    12081590000    1002 PALMERSTON AVENUE       False                627000   
18    12081592000    1004 PALMERSTON AVENUE       False                590000   
19    12081593000    1006 PALMERSTON AVENUE       False                463000   
20    12082489000           101 HOME STREET       False                355000   
21    12081696000         101 LIPTON STREET       False                339000   
22    12081952000           101 RUBY STREET       False                321000   
23    12081311000       101 SHERBURN STREET       False                289000   
24    12097805065    101-54 MARYLAND STREET       False                283000   
25    12081506000    1010 PALMERSTON AVENUE       False                552000   
26    12081613000      1010 WOLSELEY AVENUE       False               2942000   
27    12082236000      102 ARLINGTON STREET       False                215000   
28    12082918000       102 CHESTNUT STREET       False                406000   
29    12082467000           102 HOME STREET       False                333000   
30    12081983000         102 LENORE STREET       False                299000   
31    12081625000         102 LIPTON STREET       False                285000   
32    12082060000           102 RUBY STREET       False                420000   
33    12081276000       102 SHERBURN STREET       False                392000   
34    12082939000       103 CHESTNUT STREET       False                490000   
35    12081823000         103 LENORE STREET       False                317000   
36    12081695000         103 LIPTON STREET       False                448000   
37    12081953000           103 RUBY STREET       False                358000   
38    12081312000       103 SHERBURN STREET        True                292000   
39    12081434000    1030 PALMERSTON AVENUE       False                883000   
40    12081436000    1031 PALMERSTON AVENUE        True                384000   
41    12081394100       1032 PORTAGE AVENUE       False                419000   
42    12081433000    1034 PALMERSTON AVENUE       False                663000   
43    12081393100       1036 PORTAGE AVENUE       False                466000   
44    12081432000    1038 PALMERSTON AVENUE       False                475000   
45    12081392100       1038 PORTAGE AVENUE       False               1001000   
46    12082237000      104 ARLINGTON STREET       False                395000   
47    12082919000       104 CHESTNUT STREET        True                358000   
48    12082190000        104 EVANSON 

In [171]:
# YES YES YES!! Days of work!! VINDICATED!!
# Let's make this a csv

wolseley_gardens.to_csv("wolseley_gardens_final.csv", index=False)

### For analysis, see second notebook